<a href="https://colab.research.google.com/github/OlegKret/---/blob/master/Two_Phase.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [105]:
from fractions import Fraction

import numpy as np
from tabulate import tabulate

from scipy.optimize import linprog  # Import linprog

from pulp import LpMaximize, LpProblem, LpVariable, lpSum


# Set NumPy print options to display fractions globally
np.set_printoptions(precision=3, suppress=True, linewidth=100,
                    formatter={'all': lambda x: str(Fraction(x).limit_denominator())})



def create_tableau_two_phase_minimization(num_vars, num_constraints, constraint_coeffs, constraint_types, b_values):
    """
    Creates the initial tableau for the two-phase simplex method (Phase 1) for minimization problems.
    In Phase 1, the objective is to drive artificial variables out of the basis by minimizing their sum.

    Args:
    - num_vars: Number of decision variables.
    - num_constraints: Number of constraints.
    - constraint_coeffs: Coefficients of the constraints (LHS).
    - constraint_types: List of constraint types ('<=', '>=', '=').
    - b_values: RHS values for each constraint.

    Returns:
    - tableau: The initial simplex tableau for Phase 1.
    - tableau_metadata: Metadata about the tableau (all variables, basis, coeffs).
    """
    M = 1  # Set M for Phase 1 (it can be adjusted based on preference)

    # Count slack, surplus, and artificial variables
    num_slack_vars = sum(1 for t in constraint_types if t == '<=')
    num_surplus_vars = sum(1 for t in constraint_types if t == '>=')
    num_artificial_vars = sum(1 for t in constraint_types if t in ('>=', '='))

    total_columns = num_vars + num_slack_vars + num_surplus_vars + num_artificial_vars + 1  # +1 for RHS
    tableau = np.zeros((num_constraints + 1, total_columns), dtype=float)

    # List to track all variables (decision, slack, surplus, artificial)
    all_vars = [f'x{i+1}' for i in range(num_vars)]
    basis = []  # Basis stores the indices of basic variables

    # Fill the tableau with the constraints
    var_index = num_vars  # Start index for slack, surplus, and artificial variables
    for i in range(num_constraints):
        tableau[i, :num_vars] = constraint_coeffs[i]

        if constraint_types[i] == '<=':
            tableau[i, var_index] = 1  # Slack variable
            all_vars.append(f's{i + 1}')
            basis.append(var_index)  # Slack variables start in the basis
            var_index += 1

        elif constraint_types[i] == '>=':
            tableau[i, var_index] = -1  # Surplus variable
            all_vars.append(f'surplus{i + 1}')
            var_index += 1
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        elif constraint_types[i] == '=':
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        tableau[i, -1] = b_values[i]  # Fill RHS with b_values

    # Phase 1 objective: Set all decision variable coefficients to 0
    coeffs = [0] * num_vars

    # Set artificial variable coefficients to 1 for Phase 1
    for constraint_type in constraint_types:
        if constraint_type == '<=':
            coeffs.append(0)  # Slack variable coefficient = 0
        elif constraint_type == '>=':
            coeffs.append(0)  # Surplus variable coefficient = 0
            coeffs.append(1)  # Artificial variable coefficient = 1 for Phase 1
        elif constraint_type == '=':
            coeffs.append(1)  # Artificial variable coefficient = 1 for Phase 1

    # Calculate the objective row for Phase 1 (sum of artificial variables)
    for j in range(total_columns - 1):  # Exclude RHS column
        tableau[-1, j] = coeffs[j] - sum(coeffs[basis[i]] * tableau[i, j] for i in range(num_constraints))

    # Calculate RHS for the objective row (penalize artificial variables in Phase 1)
    tableau[-1, -1] = -sum(coeffs[basis[i]] * tableau[i, -1] for i in range(num_constraints))

    # Return the tableau and metadata
    tableau_metadata = {
        "all_vars": all_vars,  # List of all variable names (decision, slack, surplus, artificial)
        "basis": basis,        # Indices of the basic variables
        "coeffs": coeffs       # Coefficients for Phase 1 (artificial variables set to 1)
    }

    return tableau, tableau_metadata


def create_tableau_two_phase_maximization(num_vars, num_constraints, constraint_coeffs, constraint_types, b_values):
    """
    Creates the initial tableau for the two-phase simplex method (Phase 1) for maximization problems.

    Args:
        num_vars: Number of decision variables.
        num_constraints: Number of constraints.
        constraint_coeffs: Coefficients of the constraints.
        constraint_types: List of constraint types ('<=', '>=', '=').
        b_values: RHS values for each constraint.

    Returns:
        tableau: The initial simplex tableau for Phase 1.
        tableau_metadata: Metadata about the tableau (all variables, basis, coeffs).
    """
    import numpy as np

    M = 1  # Set M for artificial variable coefficients

    # Count slack, surplus, and artificial variables
    num_slack_vars = sum(1 for t in constraint_types if t == '<=')
    num_surplus_vars = sum(1 for t in constraint_types if t == '>=')
    num_artificial_vars = sum(1 for t in constraint_types if t in ('>=', '='))

    total_columns = num_vars + num_slack_vars + num_surplus_vars + num_artificial_vars + 1  # +1 for RHS
    tableau = np.zeros((num_constraints + 1, total_columns), dtype=float)

    # List to track all variables (decision, slack, surplus, artificial)
    all_vars = [f'x{i+1}' for i in range(num_vars)]
    basis = []  # Basis stores the indices of basic variables

    # Fill the tableau with the constraints
    var_index = num_vars  # Start index for slack, surplus, and artificial variables
    for i in range(num_constraints):
        tableau[i, :num_vars] = constraint_coeffs[i]

        if constraint_types[i] == '<=':
            tableau[i, var_index] = 1  # Slack variable
            all_vars.append(f's{i + 1}')
            basis.append(var_index)  # Slack variables start in the basis
            var_index += 1

        elif constraint_types[i] == '>=':
            tableau[i, var_index] = -1  # Surplus variable
            all_vars.append(f'surplus{i + 1}')
            var_index += 1
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        elif constraint_types[i] == '=':
            tableau[i, var_index] = 1  # Artificial variable
            all_vars.append(f'a{i + 1}')
            basis.append(var_index)  # Artificial variable starts in the basis
            var_index += 1

        tableau[i, -1] = b_values[i]  # Fill RHS with b_values

    # Phase 1 objective: Set all decision variable coefficients to 0
    coeffs = [0] * num_vars

    # Set artificial variable coefficients to -1 for Phase 1
    for constraint_type in constraint_types:
        if constraint_type == '<=':
            coeffs.append(0)  # Slack variable coefficient = 0
        elif constraint_type == '>=':
            coeffs.append(0)  # Surplus variable coefficient = 0
            coeffs.append(-1)  # Artificial variable coefficient = -1 for Phase 1
        elif constraint_type == '=':
            coeffs.append(-1)  # Artificial variable coefficient = -1 for Phase 1

    # Calculate the objective row for Phase 1 (sum of artificial variables)
    for j in range(total_columns - 1):  # Exclude RHS column
        tableau[-1, j] = coeffs[j] - sum(coeffs[basis[i]] * tableau[i, j] for i in range(num_constraints))

    # Calculate RHS for the objective row (penalize artificial variables in Phase 1)
    tableau[-1, -1] = -sum(b_values[i] for i in range(num_constraints) if 'a' in all_vars[basis[i]])

    # Return the tableau and metadata
    tableau_metadata = {
        "all_vars": all_vars,  # List of all variable names (decision, slack, surplus, artificial)
        "basis": basis,        # Indices of the basic variables
        "coeffs": coeffs       # Coefficients for Phase 1 (artificial variables set to -1)
    }

    return tableau, tableau_metadata






def transition_to_phase_2_minimization(tableau, objective_coeffs, tableau_metadata):
    """
    Transitions the tableau from Phase 1 to Phase 2 by updating the objective function
    to the original minimization problem's objective.

    Args:
    - tableau: The current tableau at the end of Phase 1.
    - objective_coeffs: The original coefficients of the minimization problem's objective function.
    - tableau_metadata: Metadata about the tableau (all variables, basis, coeffs).

    Returns:
    - tableau: The updated tableau for Phase 2.
    - tableau_metadata: Updated metadata.
    """

    num_vars = len(objective_coeffs)
    basis = tableau_metadata['basis']

    # Explicitly set the original objective coefficients for decision variables
    tableau[-1, :num_vars] = objective_coeffs

    # Calculate the reduced costs for all variables
    for j in range(len(tableau[0]) - 1):  # Exclude the RHS column
        tableau[-1, j] -= sum(tableau_metadata['coeffs'][basis[i]] * tableau[i, j]
                              for i in range(len(basis)))

    # Update the RHS for the objective row
    tableau[-1, -1] = -sum(tableau_metadata['coeffs'][basis[i]] * tableau[i, -1]
                            for i in range(len(basis)))

    # Update metadata with the original objective coefficients
    tableau_metadata['coeffs'][:num_vars] = objective_coeffs

    return tableau, tableau_metadata



def transition_to_phase_2_maximization(tableau, objective_coeffs, tableau_metadata):
    """
    Transitions the tableau from Phase 1 to Phase 2 for a maximization problem.
    """
    num_vars = len(objective_coeffs)
    basis = tableau_metadata['basis']

    # Explicitly set the original objective coefficients for decision variables
    tableau[-1, :num_vars] = objective_coeffs

    # --- Recalculate the entire objective row ---
    for j in range(len(tableau[0]) - 1):  # Exclude the RHS column
        tableau[-1, j] -= sum(tableau_metadata['coeffs'][basis[i]] * tableau[i, j]
                              for i in range(len(basis)))

    # Update the RHS for the objective row
    tableau[-1, -1] = -sum(tableau_metadata['coeffs'][basis[i]] * tableau[i, -1]
                            for i in range(len(basis)))

    # Update metadata with the original objective coefficients
    tableau_metadata['coeffs'][:num_vars] = objective_coeffs

    # For maximization, multiply the objective row by -1
    tableau[-1, :] *= -1

    return tableau, tableau_metadata







def identify_entering_column_minimization(tableau, phase=2):
    """
    Identifies the entering column based on the objective row of the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        phase: The current phase of the two-phase simplex method (1 for Phase 1, 2 for Phase 2).

    Returns:
        entering_column: The index of the entering column, or None if the optimal solution has been reached.
    """
    # Extract the objective row (last row except for the RHS value)
    objective_row = tableau[-1, :-1]

    # Set a small tolerance to avoid floating-point precision issues
    tolerance = 1e-10

    # For minimization, select the most negative coefficient below tolerance
    min_value = np.min(objective_row)

    if min_value >= -tolerance:
        return None  # No sufficiently negative coefficient found, optimal solution reached

    # Select the index of the most negative coefficient
    entering_column = np.argmin(objective_row)

    # Print the entering column index and the most negative value, adding phase information
    print(f"Phase {phase} - Entering column index: {entering_column}")
    print(f"Phase {phase} - Most negative value in objective row: {min_value}")

    return entering_column



def identify_entering_column_maximization(tableau, phase=2):
    """
    Identifies the entering column for maximization.
    """

    objective_row = tableau[-1, :-1]  # Exclude RHS
    tolerance = 1e-10  # Tolerance for comparison

    # Find the most positive value and its index
    max_value = np.max(objective_row)
    entering_column = np.argmax(objective_row)

    # Check if all reduced costs are non-positive (≤ 0)
    if max_value <= tolerance:
        return None  # Optimal solution reached

    print(f"Phase {phase} - Entering column index: {entering_column}")
    print(f"Phase {phase} - Most positive value in objective row: {max_value}")

    return entering_column


def identify_leaving_row_minimization(tableau, entering_column, phase=2):
    """
    Identifies the leaving row based on the minimum ratio test in the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        phase: The current phase of the two-phase simplex method (1 for Phase 1, 2 for Phase 2).

    Returns:
        leaving_row: The index of the leaving row, or None if the solution is unbounded.
    """
    num_rows = tableau.shape[0] - 1  # Exclude the objective row
    min_ratio = np.inf
    leaving_row = None

    # Perform the minimum ratio test
    for i in range(num_rows):
        rhs_value = tableau[i, -1]  # The RHS value for the current row
        entering_value = tableau[i, entering_column]  # Coefficient of the entering variable in this row

        # Only consider positive entering values to avoid division by zero or negative ratios
        if entering_value > 0:
            ratio = rhs_value / entering_value

            # Print the ratio for debugging purposes
            print(f"Phase {phase} - Row {i}: RHS = {rhs_value}, Entering Value = {entering_value}, Ratio = {ratio}")

            # Compare ratios, consider floating-point precision
            if ratio < min_ratio - 1e-10:
                min_ratio = ratio
                leaving_row = i
            elif abs(ratio - min_ratio) < 1e-10:
                # Optional: tie-breaking in case of degeneracy (first encountered row)
                if leaving_row is None or i < leaving_row:
                    leaving_row = i

    # Print the identified leaving row for debugging
    if leaving_row is not None:
        print(f"Phase {phase} - Identified leaving row: {leaving_row} with minimum ratio: {min_ratio}")
    else:
        print("No valid leaving row found, solution might be unbounded.")

    # If no valid leaving row is found, return None to indicate unbounded solution
    return leaving_row




def identify_leaving_row_maximization(tableau, entering_column, phase=2):
    """
    Identifies the leaving row based on the minimum ratio test in the simplex tableau for maximization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        phase: The current phase of the two-phase simplex method (1 for Phase 1, 2 for Phase 2).

    Returns:
        leaving_row: The index of the leaving row, or None if the solution is unbounded.
    """
    num_rows = tableau.shape[0] - 1  # Exclude the objective row
    min_ratio = np.inf
    leaving_row = None

    # Perform the minimum ratio test
    for i in range(num_rows):
        rhs_value = tableau[i, -1]  # The RHS value for the current row
        entering_value = tableau[i, entering_column]  # Coefficient of the entering variable in this row

        # Only consider positive entering values to avoid division by zero or negative ratios
        if entering_value > 0:
            ratio = rhs_value / entering_value

            # Print the ratio for debugging purposes
            print(f"Phase {phase} - Row {i}: RHS = {rhs_value}, Entering Value = {entering_value}, Ratio = {ratio}")

            # Compare ratios, consider floating-point precision
            if ratio < min_ratio - 1e-10:
                min_ratio = ratio
                leaving_row = i
            elif abs(ratio - min_ratio) < 1e-10:
                # Optional: tie-breaking in case of degeneracy (first encountered row)
                if leaving_row is None or i < leaving_row:
                    leaving_row = i

    # Print the identified leaving row for debugging
    if leaving_row is not None:
        print(f"Phase {phase} - Identified leaving row: {leaving_row} with minimum ratio: {min_ratio}")
    else:
        print("No valid leaving row found, solution might be unbounded.")

    # If no valid leaving row is found, return None to indicate unbounded solution
    return leaving_row





def locate_pivot_element_minimization(tableau, entering_column, leaving_row):
    """
    Locates the pivot element in the simplex tableau for minimization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.

    Returns:
        pivot_element: The value of the pivot element, or None if the leaving row is invalid.
    """
    if leaving_row is None:
        return None  # No valid pivot if no leaving row exists

    pivot_element = tableau[leaving_row, entering_column]

    # Ensure the pivot element is not zero (which would cause issues in row operations)
    if np.isclose(pivot_element, 0):
        raise ValueError(
            "Pivot element is zero indicating potential degeneracy or an error in selecting the pivot.")

    return pivot_element


def locate_pivot_element_maximization(tableau, entering_column, leaving_row):
    """
    Locates the pivot element in the simplex tableau for maximization problems.

    Args:
        tableau: The current simplex tableau.
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.

    Returns:
        pivot_element: The value of the pivot element, or None if the leaving row is invalid.
    """
    if leaving_row is None:
        return None  # No valid pivot if no leaving row exists

    pivot_element = tableau[leaving_row, entering_column]

    # Ensure the pivot element is not zero (which would cause issues in row operations)
    if np.isclose(pivot_element, 0):
        raise ValueError(
            "Pivot element is zero indicating potential degeneracy or an error in selecting the pivot.")

    return pivot_element




def update_key_row_minimization(tableau, leaving_row, pivot_element):
    """
    Updates the key row in the tableau to make the pivot element equal to 1.
    """
    tableau[leaving_row, :] /= pivot_element
    return tableau



def update_key_row_maximization(tableau, leaving_row, pivot_element):
    """
    Updates the key row in the tableau to make the pivot element equal to 1 for maximization problems.

    Args:
        tableau: The current simplex tableau.
        leaving_row: The index of the row containing the pivot element.
        pivot_element: The value of the pivot element.

    Returns:
        tableau: The updated tableau with the key row adjusted.
    """
    tableau[leaving_row, :] /= pivot_element
    return tableau




def update_non_key_rows_minimization(tableau, entering_column, leaving_row):
    """
    Updates the non-key rows in the tableau based on the new pivot element.
    """
    num_rows, num_cols = tableau.shape
    for i in range(num_rows):
        if i != leaving_row:
            factor = tableau[i, entering_column]
            tableau[i, :] -= factor * tableau[leaving_row, :]
    return tableau


def update_non_key_rows_maximization(tableau, entering_column, leaving_row):
    """
    Updates the non-key rows in the tableau based on the new pivot element.
    """
    num_rows, num_cols = tableau.shape
    for i in range(num_rows):
        if i != leaving_row:
            factor = tableau[i, entering_column]
            tableau[i, :] -= factor * tableau[leaving_row, :]

            # Additional check for surplus variables
            if tableau[i, entering_column] < 0:  # If the entering variable has a negative coefficient in this row
                tableau[i, :] *= -1  # Multiply the entire row by -1 to make the surplus variable positive

    return tableau




def update_objective_row_minimization(tableau, objective_coeffs, basis, artificial_vars, all_vars):
    """
    Updates the objective row in the simplex tableau for Phase 2 by restoring the original objective coefficients
    and recalculating the reduced costs.
    """
    num_vars = len(objective_coeffs)  # Number of decision variables
    num_basis = len(basis)

    # Restore the original coefficients for decision variables (x1, x2, x3...)
    for j in range(num_vars):
        tableau[-1, j] = objective_coeffs[j]

    # Subtract the weighted sum of the current basis (for only decision variables in the basis)
    for j in range(len(tableau[0]) - 1):  # Exclude RHS column
        weighted_sum = 0
        for i in range(num_basis):
            # Only consider decision variables for updating the objective row
            if basis[i] < num_vars:  # Ensure the variable in the basis is a decision variable
                weighted_sum += tableau[i, j] * objective_coeffs[basis[i]]
        tableau[-1, j] -= weighted_sum

    # Set the coefficients of slack, surplus, and artificial variables to 0
    for i in range(num_vars, len(all_vars)):
        tableau[-1, i] = 0

    # Recalculate RHS for the objective row
    tableau[-1, -1] = sum(tableau[i, -1] * objective_coeffs[basis[i]] for i in range(num_basis) if basis[i] < num_vars)

    # If the objective function is minimization, negate the objective row RHS value
    tableau[-1, -1] = -tableau[-1, -1]




def update_objective_row_maximization(tableau, objective_coeffs, basis, artificial_vars, all_vars):
    """
    Updates the objective row for Phase 2 of maximization.
    """
    num_vars = len(objective_coeffs)  # Number of original decision variables
    num_cols = len(tableau[0]) - 1  # Total number of columns excluding RHS

    # Restore the original coefficients for decision variables
    tableau[-1, :num_vars] = objective_coeffs

    # --- Recalculate reduced costs for ALL variables ---
    for j in range(num_cols):  # Include slack and surplus variables
        weighted_sum = 0
        for i in range(len(basis)):
            if basis[i] < num_vars:  # Consider only original decision variables in the weighted sum
                weighted_sum += tableau[i, j] * objective_coeffs[basis[i]]
        tableau[-1, j] = tableau[-1, j] - weighted_sum  # Update the objective row with reduced costs

    # Set the coefficients of artificial variables to 0
    for i in range(num_vars, len(all_vars)):
        if all_vars[i].startswith('a'):
            tableau[-1, i] = 0

    # Recalculate RHS for the objective row
    tableau[-1, -1] = sum(tableau[i, -1] * objective_coeffs[basis[i]] for i in range(len(basis)) if basis[i] < num_vars)

    # No change for maximization (we want to maximize the objective value)





def update_artificial_vars_minimization(tableau, tableau_metadata, leaving_var_idx, artificial_vars, all_vars):
    """
    Zero out artificial variable columns and remove their contribution to the objective row when they leave the basis.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: Metadata related to the tableau (coefficients, variables, basis, etc.).
        leaving_var_idx: Index of the variable that is leaving the basis.
        artificial_vars: List of indices of artificial variables.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
    """
    if leaving_var_idx in artificial_vars:
        # Zero out the column corresponding to the artificial variable
        print(f"Artificial variable {all_vars[leaving_var_idx]} is leaving the basis. Zeroing out its column.")
        tableau[:, leaving_var_idx] = 0

        # Set the artificial variable's coefficient in the objective row to 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0

        # Check if there is a corresponding surplus variable
        # This logic assumes that artificial variables may have surplus variables
        surplus_var_name = all_vars[leaving_var_idx].replace("a", "surplus")
        if surplus_var_name in all_vars:
            surplus_var_idx = all_vars.index(surplus_var_name)
            # Ensure the surplus variable is unaffected, but handle it separately if required
            if surplus_var_idx not in artificial_vars:
                print(f"Preserving surplus variable {all_vars[surplus_var_idx]} linked to artificial variable {all_vars[leaving_var_idx]}.")
                tableau[:, surplus_var_idx] = tableau[:, surplus_var_idx]

    else:
        print(f"Variable {all_vars[leaving_var_idx]} is not an artificial variable, no update required.")



def update_artificial_vars_maximization(tableau, tableau_metadata, leaving_var_idx, artificial_vars, all_vars):
    """
    Zero out artificial variable columns and remove their contribution to the objective row when they leave the basis.
    This version is for maximization problems, where artificial variables have a coefficient of -1.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: Metadata related to the tableau (coefficients, variables, basis, etc.).
        leaving_var_idx: Index of the variable that is leaving the basis.
        artificial_vars: List of indices of artificial variables.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
    """
    if leaving_var_idx in artificial_vars:
        # Zero out the column corresponding to the artificial variable
        print(f"Artificial variable {all_vars[leaving_var_idx]} is leaving the basis. Zeroing out its column.")
        tableau[:, leaving_var_idx] = 0

        # Set the artificial variable's coefficient in the objective row to 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0

        # Check if there is a corresponding surplus variable
        # This logic assumes that artificial variables may have surplus variables
        surplus_var_name = all_vars[leaving_var_idx].replace("a", "surplus")
        if surplus_var_name in all_vars:
            surplus_var_idx = all_vars.index(surplus_var_name)
            # Ensure the surplus variable is unaffected, but handle it separately if required
            if surplus_var_idx not in artificial_vars:
                print(f"Preserving surplus variable {all_vars[surplus_var_idx]} linked to artificial variable {all_vars[leaving_var_idx]}.")
                tableau[:, surplus_var_idx] = tableau[:, surplus_var_idx]

    else:
        print(f"Variable {all_vars[leaving_var_idx]} is not an artificial variable, no update required.")





def print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types, phase=None):
    """
    Prints the tableau with a header row, formatted output, and fractions.
    Includes basis variable values in the BASIS column for minimization problems.

    Args:
        tableau: The current simplex tableau.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
        basis: List of indices of the basic variables.
        coeffs: List of objective function coefficients for all variables.
        constraint_types: List of the constraint types for each row.
        phase: Optional parameter to indicate the current phase (Phase 1 or Phase 2).
    """
    # Convert tableau elements to fractions for readability
    tableau_fractions = [[Fraction(x).limit_denominator() for x in row] for row in tableau]

    # Convert fractions to strings for printing via tabulate
    tableau_strings = [[str(frac) for frac in row] for row in tableau_fractions]

    # Create the header row
    headers = ["Constraint Type", "BASIS"] + all_vars + ["RHS"]

    # Create the basis indicator row (BASIS row) - includes decision variable and objective coefficients
    basis_indicator = ["BASIS"]
    for i in range(len(tableau) - 1):  # Go through each row except the objective row
        if i < len(basis):
            basis_var_index = basis[i]
            value = coeffs[basis_var_index]  # Get the coefficient from coeffs list
            basis_indicator.append(f"{all_vars[basis_var_index]} = {value}")
        else:
            basis_indicator.append("")  # Leave empty for non-basic rows
    basis_indicator += [""] * (len(headers) - len(basis_indicator))

    # Add the objective function (coefficients row) row
    coeff_row = ["Coeff"] + [f"{Fraction(c).limit_denominator()}" for c in coeffs] + [""]

    # Combine rows with constraint types
    tableau_rows = []
    for i in range(len(tableau_strings) - 1):  # Skip the objective row
        row = [constraint_types[i], f"{all_vars[basis[i]]}"] + tableau_strings[i][:-1] + [tableau_strings[i][-1]]
        tableau_rows.append(row)

    # Add the minimization objective function row (last row in the tableau)
    objective_row = ["Minimize", ""] + tableau_strings[-1][:-1] + [tableau_strings[-1][-1]]

    # Add constraint types to the first column of each row
    for i in range(len(tableau_rows)):
        tableau_rows[i][0] = constraint_types[i]

    # Combine all rows for printing
    output_rows = []
    output_rows.append(basis_indicator)
    output_rows.append(coeff_row)
    output_rows.extend(tableau_rows)
    output_rows.append(objective_row)

    # Print the phase if provided
    if phase:
        print(f"\nSimplex Tableau - Phase {phase}")

    # Print the tableau using tabulate
    print(tabulate(output_rows, headers=headers, tablefmt="fancy_grid"))



def print_tableau_maximization(tableau, all_vars, basis, coeffs, constraint_types, phase=None):
    """
    Prints the tableau with a header row, formatted output, and fractions.
    Includes basis variable values in the BASIS column for maximization problems.

    Args:
        tableau: The current simplex tableau.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
        basis: List of indices of the basic variables.
        coeffs: List of objective function coefficients for all variables.
        constraint_types: List of the constraint types for each row.
        phase: Optional parameter to indicate the current phase (Phase 1 or Phase 2).
    """
    # Convert tableau elements to fractions for readability
    tableau_fractions = [[Fraction(x).limit_denominator() for x in row] for row in tableau]
    # Convert fractions to strings for printing via tabulate
    tableau_strings = [[str(frac) for frac in row] for row in tableau_fractions]

    # Create the header row
    headers = ["Constraint Type", "BASIS"] + all_vars + ["RHS"]

    # Create the basis indicator row (BASIS row) - includes decision variable and objective coefficients
    basis_indicator = ["BASIS"]
    for i in range(len(tableau) - 1):  # Go through each row except the objective row
        if i < len(basis):
            basis_var_index = basis[i]
            value = coeffs[basis_var_index]  # Get the coefficient from coeffs list
            basis_indicator.append(f"{all_vars[basis_var_index]} = {value}")
        else:
            basis_indicator.append("")  # Leave empty for non-basic rows
    basis_indicator += [""] * (len(headers) - len(basis_indicator))

    # Add the objective function (coefficients row) row
    coeff_row = ["Coeff"] + [f"{Fraction(c).limit_denominator()}" for c in coeffs] + [""]

    # Combine rows with constraint types
    tableau_rows = []
    for i in range(len(tableau_strings) - 1):  # Skip the objective row
        row = [constraint_types[i], f"{all_vars[basis[i]]}"] + tableau_strings[i][:-1] + [tableau_strings[i][-1]]
        tableau_rows.append(row)

    # Add the maximization objective function row (last row in the tableau)
    objective_row = ["Maximize", ""] + tableau_strings[-1][:-1] + [tableau_strings[-1][-1]]

    # Add constraint types to the first column of each row
    for i in range(len(tableau_rows)):
        tableau_rows[i][0] = constraint_types[i]

    # Combine all rows for printing
    output_rows = []
    output_rows.append(basis_indicator)
    output_rows.append(coeff_row)
    output_rows.extend(tableau_rows)
    output_rows.append(objective_row)

    # Print the phase if provided
    if phase:
        print(f"\nSimplex Tableau - Phase {phase}")

    # Print the tableau using tabulate
    print(tabulate(output_rows, headers=headers, tablefmt="fancy_grid"))



def print_problem_summary_minimization(objective_function, constraints, all_vars, tableau, basis, phase=None):
    """
    Prints a summary of the linear programming minimization problem with nicer formatting,
    including slack/surplus/artificial variables in the constraints, and shows the final
    objective function with the values of the basic variables.

    Args:
        objective_function: Coefficients of the objective function.
        constraints: List of constraints, each containing 'coeffs', 'type', and 'rhs'.
        all_vars: List of all variables (decision, slack, surplus, artificial).
        tableau: The final simplex tableau.
        basis: List of indices of the basic variables.
        phase: The current phase (1 or 2) of the two-phase simplex method.
    """

    # Print phase header if provided
    if phase:
        print(f"\nPhase {phase} Summary")

    # Print objective function header
    print("\nObjective Function:")
    obj_str = "Minimize Z = "
    objective_terms = []

    # Build the objective function string with variable values from the tableau
    for i, var_idx in enumerate(basis):
        coef = objective_function[var_idx] if phase == 2 else 0  # Coefficients set to 0 in Phase 1
        if coef != 0 or phase == 1:  # Include Phase 1 artificial variables in the summary
            var_value = tableau[i, -1]  # Get the value from the tableau
            objective_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Add artificial variable terms (if any) for Phase 1 minimization with Big M
    artificial_terms = []
    if phase == 1:
        for var_idx in range(len(all_vars)):
            if all_vars[var_idx].startswith('a'):
                coef = 1  # In Phase 1, artificial variable coefficients are set to 1
                var_value = tableau[basis.index(var_idx), -1] if var_idx in basis else 0
                artificial_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Combine the objective function and artificial terms
    obj_str += " + ".join(objective_terms + artificial_terms)
    print(obj_str)

    # Print constraints
    print("\nConstraints:")
    for i, constraint in enumerate(constraints):  # Access constraints from the argument
        # Build the constraint string with coefficients and variables
        constraint_str = " + ".join(
            f"{Fraction(constraint['coeffs'][j]).limit_denominator()}*{all_vars[j]}"
            for j in range(len(constraint['coeffs']))
        )
        # Add slack, surplus, or artificial variable depending on the constraint type
        constraint_str += {
            "<=": f" + s{i + 1}",
            ">=": f" - surplus{i + 1} + a{i + 1}",
            "=": f" + a{i + 1}",
        }[constraint['type']]
        # Add the right-hand side of the constraint
        constraint_str += f" = {Fraction(constraint['rhs']).limit_denominator()}"
        print(f"{i + 1}. {constraint_str}")

    # Additional Phase 1 details (if artificial variables are still in the basis)
    if phase == 1:
        print("\nArtificial Variables in Phase 1:")
        for var_idx in artificial_terms:
            print(f"Artificial variable {var_idx} is present in the basis.")




def print_problem_summary_maximization(objective_function, constraints, all_vars, tableau, basis, phase=None):
    """
    Prints a summary of the linear programming maximization problem with nicer formatting,
    including slack/surplus/artificial variables in the constraints, and shows the final
    objective function with the values of the basic variables.

    Args:
        objective_function: Coefficients of the objective function.
        constraints: List of constraints, each containing 'coeffs', 'type', and 'rhs'.
        all_vars: List of all variables (decision, slack, surplus, artificial).
        tableau: The final simplex tableau.
        basis: List of indices of the basic variables.
        phase: The current phase (1 or 2) of the two-phase simplex method.
    """

    # Print phase header if provided
    if phase:
        print(f"\nPhase {phase} Summary")

    # Print objective function header
    print("\nObjective Function:")
    obj_str = "Maximize Z = "
    objective_terms = []

    # Build the objective function string with variable values from the tableau
    for i, var_idx in enumerate(basis):
        coef = objective_function[var_idx] if phase == 2 else 0  # Coefficients set to 0 in Phase 1
        if coef != 0 or phase == 1:  # Include Phase 1 artificial variables in the summary
            var_value = tableau[i, -1]  # Get the value from the tableau
            objective_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Add artificial variable terms (if any) for Phase 1 maximization
    artificial_terms = []
    if phase == 1:
        for var_idx in range(len(all_vars)):
            if all_vars[var_idx].startswith('a'):
                coef = -1  # In Phase 1, artificial variable coefficients are set to -1 for maximization
                var_value = tableau[basis.index(var_idx), -1] if var_idx in basis else 0
                artificial_terms.append(f"{coef}*{all_vars[var_idx]} = {coef * var_value}")

    # Combine the objective function and artificial terms
    obj_str += " + ".join(objective_terms + artificial_terms)
    print(obj_str)

    # Print constraints
    print("\nConstraints:")
    for i, constraint in enumerate(constraints):  # Access constraints from the argument
        # Build the constraint string with coefficients and variables
        constraint_str = " + ".join(
            f"{Fraction(constraint['coeffs'][j]).limit_denominator()}*{all_vars[j]}"
            for j in range(len(constraint['coeffs']))
        )
        # Add slack, surplus, or artificial variable depending on the constraint type
        constraint_str += {
            "<=": f" + s{i + 1}",
            ">=": f" - surplus{i + 1} + a{i + 1}",
            "=": f" + a{i + 1}",
        }[constraint['type']]
        # Add the right-hand side of the constraint
        constraint_str += f" = {Fraction(constraint['rhs']).limit_denominator()}"
        print(f"{i + 1}. {constraint_str}")

    # Additional Phase 1 details (if artificial variables are still in the basis)
    if phase == 1:
        print("\nArtificial Variables in Phase 1:")
        for var_idx in artificial_terms:
            print(f"Artificial variable {var_idx} is present in the basis.")




def extract_solution_minimization(tableau_metadata, phase):
    """
    Extracts the solution from the simplex tableau for a minimization problem.
    Handles degeneracy, unboundedness, and provides more robust error handling.

    Args:
        tableau_metadata: A dictionary containing the tableau, basis, all_vars, and other related information.
        phase: The current phase (1 or 2) of the two-phase simplex method.

    Returns:
        solution: A dictionary containing the solution status, objective value, variable values,
                  and any relevant messages or warnings.
    """
    tableau = tableau_metadata.get('tableau', None)
    basis = tableau_metadata.get('basis', None)
    all_vars = tableau_metadata.get('all_vars', [])
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]
    num_vars = len(tableau_metadata.get('coeffs', []))  # Number of original decision variables

    # If any key is missing, return an empty solution dictionary
    if tableau is None or basis is None or len(all_vars) == 0:
        return {"status": "error", "message": "Tableau or metadata incomplete", "variable_values": {}, "objective_value": None}

    solution = {"status": None, "objective_value": None, "variable_values": {}, "message": ""}

    # Handle Phase 1: Focus on removing artificial variables
    if phase == 1:
        # Check for artificial variables still in the basis
        artificial_in_basis = any(basis_var in artificial_vars for basis_var in basis)
        if artificial_in_basis:
            artificial_values = {all_vars[i]: tableau[basis.index(i), -1] for i in artificial_vars if i in basis}
            solution["status"] = "phase_1_incomplete"
            solution["message"] = "Artificial variables are still in the basis."
            solution["artificial_values"] = artificial_values
            return solution

        solution["status"] = "phase_1_complete"
        solution["message"] = "Artificial variables removed. Ready for Phase 2."

    # Handle Phase 2: Extract the solution based on the original objective function
    if phase == 2:
        # Check for artificial variables in the basis (should not happen in Phase 2)
        if any(basis_var in artificial_vars for basis_var in basis):
            solution["status"] = "infeasible"
            solution["message"] = "Artificial variable still in the basis, problem is infeasible."
            return solution

        # Check for unboundedness
        for j in range(len(tableau[0]) - 1):  # Iterate over columns (excluding RHS)
            if tableau[-1, j] < 0 and all(tableau[i, j] <= 0 for i in range(len(tableau) - 1)):
                solution["status"] = "unbounded"
                solution["message"] = "Unbounded solution detected."
                return solution

        # Extract variable values (including non-basic variables)
        for i, var_name in enumerate(all_vars):
            if i in basis:
                row = basis.index(i)
                solution["variable_values"][var_name] = Fraction(tableau[row, -1]).limit_denominator()
                if i < num_vars and solution["variable_values"][var_name] == 0:  # Check for degeneracy
                    solution["message"] += "Degeneracy detected. "
            else:
                solution["variable_values"][var_name] = 0  # Non-basic variables have value 0

        # Calculate the optimal objective function value for minimization
        solution["objective_value"] = - Fraction(tableau[-1, -1]).limit_denominator()  # Negate for minimization

        solution["status"] = "optimal"
        return solution

    # If for some reason no phase is recognized
    solution["status"] = "error"
    solution["message"] = "Unable to extract the solution. Check the tableau."
    return solution




def extract_solution_maximization(tableau_metadata, phase):
    """
    Extracts the solution from the simplex tableau for a maximization problem.
    """
    tableau = tableau_metadata.get('tableau', None)
    basis = tableau_metadata.get('basis', None)
    all_vars = tableau_metadata.get('all_vars', [])
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]
    num_vars = len(tableau_metadata.get('coeffs', []))

    # Error handling for missing keys
    if tableau is None or basis is None or len(all_vars) == 0:
        return {"status": "error", "message": "Tableau or metadata incomplete",
                "variable_values": {}, "objective_value": None}

    solution = {"status": None, "objective_value": None, "variable_values": {}, "message": ""}

    if phase == 1:
        # Check for artificial variables in the basis
        artificial_in_basis = any(basis_var in artificial_vars for basis_var in basis)
        if artificial_in_basis:
            artificial_values = {all_vars[i]: tableau[basis.index(i), -1] for i in artificial_vars if i in basis}
            solution["status"] = "phase_1_incomplete"
            solution["message"] = "Artificial variables are still in the basis."
            solution["artificial_values"] = artificial_values
            return solution

        solution["status"] = "phase_1_complete"
        solution["message"] = "Artificial variables removed. Ready for Phase 2."
        return solution

    if phase == 2:
        # Check for artificial variables in the basis (shouldn't happen in Phase 2)
        if any(basis_var in artificial_vars for basis_var in basis):
            solution["status"] = "infeasible"
            solution["message"] = "Artificial variable in the basis in Phase 2. Infeasible."
            return solution

        # Check for unboundedness (for maximization, all values in the column should be <= 0)
        for j in range(len(tableau[0]) - 1):
            if tableau[-1, j] > 0 and all(tableau[i, j] <= 0 for i in range(len(tableau) - 1)):
                solution["status"] = "unbounded"
                solution["message"] = "Unbounded solution detected."
                return solution

        # Extract variable values
        variable_values = {}
        for i, var_name in enumerate(all_vars):
            if i in basis:
                row = basis.index(i)
                variable_values[var_name] = Fraction(tableau[row, -1]).limit_denominator()
                if i < num_vars and variable_values[var_name] == 0:  # Check for degeneracy
                    solution["message"] += "Degeneracy detected. "
            else:
                variable_values[var_name] = 0

        # Calculate the objective function value (no negation for maximization)
        objective_value = Fraction(tableau[-1, -1]).limit_denominator()

        solution["status"] = "optimal"
        solution["objective_value"] = objective_value
        solution["variable_values"] = variable_values
        return solution

    solution["status"] = "error"
    solution["message"] = "Unable to extract the solution. Check the tableau."
    return solution





def update_tableau_for_basis_change_minimization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis and tableau when an entering variable replaces a leaving variable in a minimization problem.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: A dictionary containing tableau metadata (coefficients, variables, basis, etc.).
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.
        artificial_vars: List of indices of artificial variables.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
    """

    # Handle the basis change: Replace the leaving variable with the entering variable
    leaving_var_idx = tableau_metadata["basis"][leaving_row]
    tableau_metadata["basis"][leaving_row] = entering_column
    new_basis = tableau_metadata["basis"]

    # Zero out artificial variables when they leave the basis
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0  # Zero out the column corresponding to the artificial variable
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Set the coefficient to zero to remove the variable's contribution

    # Ensure that artificial variables do not re-enter the basis once they leave
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the coefficient of the artificial variable to zero

    # Update the objective row after the basis change
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], new_basis, artificial_vars, all_vars)



def update_tableau_for_basis_change_maximization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis and tableau when an entering variable replaces a leaving variable in a maximization problem.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: A dictionary containing tableau metadata (coefficients, variables, basis, etc.).
        entering_column: The index of the entering column.
        leaving_row: The index of the leaving row.
        artificial_vars: List of indices of artificial variables.
        all_vars: List of all variable names (decision, slack, surplus, artificial).
    """

    # Handle the basis change: Replace the leaving variable with the entering variable
    leaving_var_idx = tableau_metadata["basis"][leaving_row]
    tableau_metadata["basis"][leaving_row] = entering_column
    new_basis = tableau_metadata["basis"]

    # Zero out artificial variables when they leave the basis
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0  # Zero out the column corresponding to the artificial variable
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Set the coefficient to zero to remove the variable's contribution

    # Ensure that artificial variables do not re-enter the basis once they leave
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the coefficient of the artificial variable to zero

    # Update the objective row after the basis change
    update_objective_row_maximization(tableau, tableau_metadata["coeffs"], new_basis, artificial_vars, all_vars)




def check_penalty_and_feasibility_minimization(tableau, all_vars, artificial_vars, M, tableau_metadata):
    """
    Check the final tableau for artificial variables and calculate the penalty for minimization problems.

    Args:
        tableau: The final simplex tableau.
        all_vars: The list of all variable names.
        artificial_vars: List of indices of artificial variables.
        M: The large penalty value used in the Big M method for minimization.
        tableau_metadata: A dictionary containing the tableau, basis, and other related information.

    Returns:
        penalty_m_term: The accumulated coefficient of M in the objective function.
        constant_value: The constant part of the objective value (RHS).
        feasible: True if no artificial variables remain in the basis, False if they do.
    """
    penalty_m_term = 0  # Represents the M-term coefficient for artificial variables
    constant_value = tableau[-1, -1]  # Start with the constant from the RHS of the objective row
    feasible = True  # Assume the solution is feasible unless proven otherwise

    # Debugging: Print artificial variables and their values
    print("\nChecking for artificial variables in the basis:")

    # Iterate over all artificial variables to check if they are still in the basis
    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            # If an artificial variable is still in the basis, it contributes to the penalty
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]

            # Print debug information about the artificial variable and its value
            print(f"Artificial variable {all_vars[i]} is in the basis with value {value_in_basis}.")

            # For minimization, the penalty applies if the artificial variable has a positive value
            if value_in_basis > 0:
                penalty_m_term += value_in_basis  # Accumulate the penalty (positive value * M)
                feasible = False  # The solution is not feasible if artificial variables remain

    # Correct the objective value by adding the penalty (for minimization, we use +M)
    if not feasible:
        print(f"Penalty term due to artificial variables: {penalty_m_term} * M")
        constant_value += penalty_m_term * M  # Add the penalty term to the constant part of the objective value
        return penalty_m_term, constant_value, False  # Return the penalty, constant value, and infeasibility flag
    else:
        return 0, constant_value, True  # No penalty, solution is feasible


def check_penalty_and_feasibility_maximization(tableau, all_vars, artificial_vars, M, tableau_metadata):
    """
    Check the final tableau for artificial variables and calculate the penalty for maximization problems.

    Args:
        tableau: The final simplex tableau.
        all_vars: The list of all variable names.
        artificial_vars: List of indices of artificial variables.
        M: The large penalty value used in the Big M method for maximization.
        tableau_metadata: A dictionary containing the tableau, basis, and other related information.

    Returns:
        penalty_m_term: The accumulated coefficient of M in the objective function.
        constant_value: The constant part of the objective value (RHS).
        feasible: True if no artificial variables remain in the basis, False if they do.
    """
    penalty_m_term = 0  # Represents the M-term coefficient for artificial variables
    constant_value = tableau[-1, -1]  # Start with the constant from the RHS of the objective row
    feasible = True  # Assume the solution is feasible unless proven otherwise

    # Debugging: Print artificial variables and their values
    print("\nChecking for artificial variables in the basis:")

    # Iterate over all artificial variables to check if they are still in the basis
    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            # If an artificial variable is still in the basis, it contributes to the penalty
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]

            # Print debug information about the artificial variable and its value
            print(f"Artificial variable {all_vars[i]} is in the basis with value {value_in_basis}.")

            # For maximization, the penalty applies if the artificial variable has a negative value
            if value_in_basis < 0:
                penalty_m_term += abs(value_in_basis)  # Accumulate the penalty (negative value * M)
                feasible = False  # The solution is not feasible if artificial variables remain

    # Correct the objective value by subtracting the penalty (for maximization, we use -M)
    if not feasible:
        print(f"Penalty term due to artificial variables: {penalty_m_term} * M")
        constant_value -= penalty_m_term * M  # Subtract the penalty term from the constant part of the objective value
        return penalty_m_term, constant_value, False  # Return the penalty, constant value, and infeasibility flag
    else:
        return 0, constant_value, True  # No penalty, solution is feasible


def update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis after performing a pivot, replacing the leaving variable with the entering variable
    and updating the value.
    """
    # Identify the leaving variable's index in the basis
    leaving_var_idx = tableau_metadata["basis"][leaving_row]

    # Replace the leaving variable with the entering variable
    tableau_metadata["basis"][leaving_row] = entering_column

    # If the leaving variable is artificial, zero out its column and set its coefficient to 0
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Ensure the coefficient is zeroed out

    # Ensure that the artificial variable never re-enters the basis once it leaves
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the artificial variable's coefficient to zero

    # Debugging: Print when an artificial variable leaves the basis
    if leaving_var_idx in artificial_vars:
        print(f"Artificial variable {all_vars[leaving_var_idx]} has left the basis.")

    # Update the objective row and other rows based on the new basis
    update_objective_row_minimization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)



def update_basis_with_values_maximization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars):
    """
    Updates the basis after performing a pivot, replacing the leaving variable with the entering variable
    and updating the value for maximization problems.
    """
    # Identify the leaving variable's index in the basis
    leaving_var_idx = tableau_metadata["basis"][leaving_row]

    # Replace the leaving variable with the entering variable
    tableau_metadata["basis"][leaving_row] = entering_column

    # If the leaving variable is artificial, zero out its column and set its coefficient to 0
    if leaving_var_idx in artificial_vars:
        tableau[:, leaving_var_idx] = 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Ensure the coefficient is zeroed out

    # Ensure that the artificial variable never re-enters the basis once it leaves
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set the artificial variable's coefficient to zero

    # Debugging: Print when an artificial variable leaves the basis
    if leaving_var_idx in artificial_vars:
        print(f"Artificial variable {all_vars[leaving_var_idx]} has left the basis.")

    # Update the objective row and other rows based on the new basis for maximization
    update_objective_row_maximization(tableau, tableau_metadata["coeffs"], tableau_metadata["basis"], artificial_vars, all_vars)





def check_constraint_violations(solution, constraint_coeffs, constraint_types, b_values, debug=False):
    """
    Checks for constraint violations by comparing LHS and RHS values for each constraint.
    Handles cases where the solution or variable_values is None.

    Args:
        solution: The current solution values for the variables.
        constraint_coeffs: List of coefficients for each constraint (LHS).
        constraint_types: List of constraint types ('<=', '>=', '=').
        b_values: List of RHS values for each constraint.
        debug: If True, prints additional debugging information.

    Returns:
        A list of violations. Each violation is represented by a tuple
        (index, LHS value, RHS value, constraint type).
    """
    violations = []

    # Handle cases where solution or variable_values is None
    if solution is None or solution.get('variable_values') is None:
        return []  # Or handle it differently based on your needs

    # Ensure the constraints lists have matching lengths
    num_constraints = min(len(constraint_coeffs), len(constraint_types), len(b_values))

    # Iterate through each constraint and calculate the LHS
    for i in range(num_constraints):
        coeffs = constraint_coeffs[i]
        lhs_value = sum(coeffs[j] * solution['variable_values'].get(f"x{j+1}", 0) for j in range(len(coeffs)))
        rhs_value = b_values[i]

        # Debugging: Print LHS and RHS comparison
        if debug:
            print(f"Constraint {i + 1}: LHS = {lhs_value}, RHS = {rhs_value}, Type: {constraint_types[i]}")

        # Check for violations based on constraint type
        if constraint_types[i] == '<=' and lhs_value > rhs_value:
            violations.append((i, lhs_value, rhs_value, '<='))
        elif constraint_types[i] == '>=' and lhs_value < rhs_value:
            violations.append((i, lhs_value, rhs_value, '>='))
        elif constraint_types[i] == '=' and abs(lhs_value - rhs_value) > 1e-9:
            violations.append((i, lhs_value, rhs_value, '='))

    return violations


def check_constraint_violations_maximization(solution, constraint_coeffs, constraint_types, b_values, debug=False):
    """
    Checks for constraint violations by comparing LHS and RHS values for each constraint in a maximization problem.
    Handles cases where the solution or variable_values is None.

    Args:
        solution: The current solution values for the variables.
        constraint_coeffs: List of coefficients for each constraint (LHS).
        constraint_types: List of constraint types ('<=', '>=', '=').
        b_values: List of RHS values for each constraint.
        debug: If True, prints additional debugging information.

    Returns:
        A list of violations. Each violation is represented by a tuple
        (index, LHS value, RHS value, constraint type).
    """
    violations = []

    # Handle cases where solution or variable_values is None
    if solution is None or solution.get('variable_values') is None:
        return []  # Return empty list if no solution or variable values exist

    # Ensure the constraints lists have matching lengths
    num_constraints = min(len(constraint_coeffs), len(constraint_types), len(b_values))

    # Iterate through each constraint and calculate the LHS
    for i in range(num_constraints):
        coeffs = constraint_coeffs[i]
        lhs_value = sum(coeffs[j] * solution['variable_values'].get(f"x{j+1}", 0) for j in range(len(coeffs)))
        rhs_value = b_values[i]

        # Debugging: Print LHS and RHS comparison
        if debug:
            print(f"Constraint {i + 1}: LHS = {lhs_value}, RHS = {rhs_value}, Type: {constraint_types[i]}")

        # Check for violations based on constraint type
        if constraint_types[i] == '<=' and lhs_value > rhs_value:
            violations.append((i, lhs_value, rhs_value, '<='))  # LHS exceeds RHS
        elif constraint_types[i] == '>=' and lhs_value < rhs_value:
            violations.append((i, lhs_value, rhs_value, '>='))  # LHS less than RHS
        elif constraint_types[i] == '=' and abs(lhs_value - rhs_value) > 1e-9:
            violations.append((i, lhs_value, rhs_value, '='))  # LHS not equal to RHS within tolerance

    return violations




def print_violation_report(violations, all_vars, constraint_coeffs):
    """
    Prints a detailed report of the constraint violations.

    Args:
        violations: A list of constraint violations.
        all_vars: List of variable names.
        constraint_coeffs: Coefficients for each constraint.
    """
    print("\nConstraint Violations Detected:")
    for (idx, lhs_value, rhs_value, constraint_type) in violations:
        # Construct the constraint as a string using the variable names and coefficients
        constraint_str = " + ".join(f"{coeff}*{all_vars[j]}" for j, coeff in enumerate(constraint_coeffs[idx]) if coeff != 0)
        lhs_value = round(lhs_value, 6)  # Round LHS for readability
        rhs_value = round(rhs_value, 6)  # Round RHS for readability

        # Print the violation message with proper formatting
        print(f"Constraint {idx + 1}: {constraint_str} {constraint_type} {rhs_value}, but LHS = {lhs_value}")


def print_violation_report_maximization(violations, all_vars, constraint_coeffs):
    """
    Prints a detailed report of the constraint violations for a maximization problem.

    Args:
        violations: A list of constraint violations.
        all_vars: List of variable names.
        constraint_coeffs: Coefficients for each constraint.
    """
    print("\nConstraint Violations Detected:")
    for (idx, lhs_value, rhs_value, constraint_type) in violations:
        # Construct the constraint as a string using the variable names and coefficients
        constraint_str = " + ".join(f"{coeff}*{all_vars[j]}" for j, coeff in enumerate(constraint_coeffs[idx]) if coeff != 0)
        lhs_value = round(lhs_value, 6)  # Round LHS for readability
        rhs_value = round(rhs_value, 6)  # Round RHS for readability

        # Print the violation message with proper formatting for maximization
        print(f"Constraint {idx + 1}: {constraint_str} {constraint_type} {rhs_value}, but LHS = {lhs_value}")



def generalized_penalty_check(tableau, all_vars, artificial_vars, tableau_metadata):
    """
    Check the final tableau for artificial variables after Phase 1.

    Args:
        tableau: The final simplex tableau.
        all_vars: The list of all variable names.
        artificial_vars: List of indices of artificial variables.
        tableau_metadata: A dictionary containing the tableau, basis, and other related information.

    Returns:
        feasible: True if no artificial variables remain in the basis, False if they do.
    """
    feasible = True  # Assume feasible unless an artificial variable is still in the basis

    # Iterate over all artificial variables to check if they are still in the basis
    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]

            # Print debug information about the artificial variable and its value
            print(f"Artificial variable {all_vars[i]} is in the basis with value {value_in_basis}.")

            # If any artificial variable is still in the basis, the solution is not feasible
            feasible = False
            break  # No need to continue checking, we know the solution is infeasible

    if feasible:
        print("No artificial variables remain in the basis. Proceeding to Phase 2.")
    else:
        print("Artificial variables remain in the basis. Solution is infeasible.")

    return feasible



def generalized_penalty_check_maximization(tableau, all_vars, artificial_vars, tableau_metadata):
    """
    Check the final tableau for artificial variables after Phase 1 for a maximization problem.

    Args:
        tableau: The final simplex tableau.
        all_vars: The list of all variable names.
        artificial_vars: List of indices of artificial variables.
        tableau_metadata: A dictionary containing the tableau, basis, and other related information.

    Returns:
        feasible: True if no artificial variables remain in the basis, False if they do.
    """
    feasible = True  # Assume feasible unless an artificial variable is still in the basis

    # Iterate over all artificial variables to check if they are still in the basis
    for i in artificial_vars:
        if i in tableau_metadata["basis"]:
            row_idx = tableau_metadata["basis"].index(i)
            value_in_basis = tableau[row_idx, -1]

            # Print debug information about the artificial variable and its value
            print(f"Artificial variable {all_vars[i]} is in the basis with value {value_in_basis}.")

            # If any artificial variable is still in the basis, the solution is not feasible
            feasible = False
            break  # No need to continue checking, we know the solution is infeasible

    if feasible:
        print("No artificial variables remain in the basis. Proceeding to Phase 2.")
    else:
        print("Artificial variables remain in the basis. Solution is infeasible.")

    return feasible




def two_phase_simplex_minimization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values):
    """
    Performs the two-phase simplex method to solve a linear programming problem.

    Args:
        num_vars: Number of decision variables.
        num_constraints: Number of constraints.
        objective_coeffs: Coefficients of the objective function.
        constraint_coeffs: Coefficients of the constraints.
        constraint_types: Types of the constraints ('<=', '>=', or '=').
        b_values: Right-hand side values of the constraints.

    Returns:
        None. Prints the solution and the optimal objective value.
    """
    from pulp import LpMinimize, LpProblem, LpVariable, lpSum

    # Phase 1: Create the initial tableau and solve Phase 1
    tableau, tableau_metadata = create_tableau_two_phase_minimization(
        num_vars, num_constraints, constraint_coeffs, constraint_types, b_values
    )

    tableau_metadata["constraints"] = {
        "coeffs": constraint_coeffs,
        "types": constraint_types,
        "rhs": b_values
    }

    # Add tableau to tableau_metadata
    tableau_metadata["tableau"] = tableau

    basis = tableau_metadata["basis"]
    all_vars = tableau_metadata["all_vars"]
    coeffs = tableau_metadata["coeffs"]

    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    print("\nInitial Tableau (Phase 1):")
    print_tableau_minimization(tableau, all_vars, basis, coeffs, constraint_types, phase=1)

    # Phase 1 simplex iterations to remove artificial variables
    is_optimal_phase1 = False
    is_unbounded = False
    iteration_count = 0

    # Initialize is_feasible here, before the first while loop
    is_feasible = False

    while not is_optimal_phase1 and not is_unbounded:
        entering_column = identify_entering_column_minimization(tableau)
        if entering_column is None:
            is_optimal_phase1 = True
            break

        leaving_row = identify_leaving_row_minimization(tableau, entering_column)
        if leaving_row is None:
            is_unbounded = True
            break

        pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
        tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
        tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

        update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

        print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=1)


        # Check if the solution is feasible after this iteration
        if check_feasibility_after_iteration(tableau, tableau_metadata, num_vars, constraint_coeffs, constraint_types, b_values):
            is_optimal_phase1 = True  # Stop further iterations, proceed to Phase 2

        iteration_count += 1
        if iteration_count > MAX_ITERATIONS:
            print("Max iterations reached in Phase 1, stopping.")
            break

    # Check if Phase 1 is successful (this will now assign a value to is_feasible)
    is_feasible = generalized_penalty_check(tableau, all_vars, artificial_vars, tableau_metadata)

    if not is_feasible:
        print("Phase 1 failed: Infeasible solution. Relaxing constraints...")

        # Relax the constraints (directly, without the violation report)
        relaxed_b_values = relax_constraints(constraint_coeffs, constraint_types, b_values)

        # Start with an initial relaxation factor
        relaxation_factor = 0.1

        # Try increasing the relaxation factor until a feasible solution is found
        while not is_feasible and relaxation_factor <= 0.5:
            # Re-run the two-phase simplex method with relaxed constraints
            tableau, tableau_metadata = create_tableau_two_phase_minimization(
                num_vars, num_constraints, constraint_coeffs, constraint_types, relaxed_b_values
            )

            # Add the 'constraints' key to the new tableau_metadata
            tableau_metadata["constraints"] = {
                "coeffs": constraint_coeffs,
                "types": constraint_types,
                "rhs": relaxed_b_values  # Use the relaxed values here
            }

            # Check if the solution is feasible now
            is_feasible = generalized_penalty_check(tableau, all_vars, artificial_vars, tableau_metadata)

            # Increase the relaxation factor and relax constraints further if still infeasible
            if not is_feasible:
                relaxation_factor += 0.1
                relaxed_b_values = relax_constraints(constraint_coeffs, constraint_types, relaxed_b_values, relaxation_factor)

        if not is_feasible:
            print("\nStill infeasible after trying various relaxation factors. Consider further analysis.")


    # if not is_feasible:
    #     print("Phase 1 failed: Infeasible solution. Applying penalty method...")

    #     # Initial penalty parameters
    #     penalty_parameters = [1] * num_constraints

    #     # Add penalty terms to the objective function (modifies tableau and metadata in place)
    #     new_objective_coeffs, _, _, _ = add_penalty_terms(  # No need to use the returned constraint data
    #         objective_coeffs, constraint_coeffs, constraint_types, b_values, penalty_parameters
    #     )

    #     # Update the objective coefficients in the tableau
    #     tableau[-1, :num_vars] = new_objective_coeffs

    #     # Update the objective coefficients in the metadata
    #     tableau_metadata['coeffs'] = new_objective_coeffs

    #     print("\nRetrying with penalty method:")


    if not is_feasible:
        print("Phase 1 failed: Infeasible solution. Applying penalty method...")

        # Initial penalty parameters
        penalty_parameters = [1] * num_constraints

        # Add penalty terms to the objective function (modifies tableau and metadata in place)
        add_penalty_terms(tableau, tableau_metadata, penalty_parameters)

        print("\nRetrying with penalty method:")

    # Phase 1 completed successfully, now move to Phase 2
    if is_feasible:
        print("\nPhase 1 completed successfully, proceeding to Phase 2.")

        # Transition to Phase 2
        tableau, tableau_metadata = transition_to_phase_2_minimization(tableau, objective_coeffs, tableau_metadata)

        # Update tableau_metadata["coeffs"] with the original objective coefficients
        tableau_metadata["coeffs"][:num_vars] = objective_coeffs

        # Update the objective row for Phase 2
        update_objective_row_minimization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

        print("\nStarting Phase 2 with updated objective coefficients:")
        print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)

        # Phase 2 simplex iterations
        is_optimal_phase2 = False
        iteration_count = 0
        while not is_optimal_phase2 and not is_unbounded:
            entering_column = identify_entering_column_minimization(tableau)
            if entering_column is None:
                is_optimal_phase2 = True
                break

            leaving_row = identify_leaving_row_minimization(tableau, entering_column)
            if leaving_row is None:
                is_unbounded = True
                break

            pivot_element = locate_pivot_element_minimization(tableau, entering_column, leaving_row)
            tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
            tableau = update_non_key_rows_minimization(tableau, entering_column, leaving_row)

            update_basis_with_values(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

            # Ensure the objective row is updated after each pivot in Phase 2
            update_objective_row_minimization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

            print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)

            iteration_count += 1
            if iteration_count > MAX_ITERATIONS:
                print("Max iterations reached in Phase 2, stopping.")
                break

        # Extract and print the final solution after Phase 2
        if is_optimal_phase2:
            print("\nPhase 2 - Optimal Solution Reached")
            solution = extract_solution_minimization(tableau_metadata, 2)
            print(f"Optimal Objective Value: Z = {solution['objective_value']}")
            print("Solution:", solution['variable_values'])

            # Check for alternative optimal solutions
            alternative_solutions = []
            for j in range(num_vars):  # Check decision variables
                if j not in tableau_metadata["basis"] and tableau[-1, j] == 0:  # Non-basic with zero reduced cost
                    print("Alternative optimal solutions exist!")

                    # Store the current optimal solution
                    alternative_solutions.append(solution['variable_values'].copy())

                    # Perform a pivot to find the alternative solution
                    leaving_row = identify_leaving_row_minimization(tableau, j, phase=2)
                    if leaving_row is not None:
                        pivot_element = locate_pivot_element_minimization(tableau, j, leaving_row)
                        tableau = update_key_row_minimization(tableau, leaving_row, pivot_element)
                        tableau = update_non_key_rows_minimization(tableau, j, leaving_row)
                        update_basis_with_values(tableau, tableau_metadata, j, leaving_row, artificial_vars, all_vars)
                        update_objective_row_minimization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

                        # Extract the alternative solution
                        alternative_solution = extract_solution_minimization(tableau_metadata, 2)


                        alternative_solutions.append(alternative_solution['variable_values'].copy())

            # Print alternative solutions (if found)
            if alternative_solutions:
                print("\nAlternative Optimal Solutions:")
                for sol in alternative_solutions:
                    print(sol)

            # Print the final tableau
            print("\nFinal Tableau (Phase 2):")
            print_tableau_minimization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)

    else:
        print("Phase 1 failed: Infeasible solution, artificial variables remain in the basis.")

    # Solve with Pulp to compare
    model = LpProblem(name="Minimization_Problem", sense=LpMinimize)
    x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
    model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))
    for i in range(num_constraints):
        if constraint_types[i] == '<=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
        elif constraint_types[i] == '>=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
        elif constraint_types[i] == '=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

    model.solve()

    print("\nOptimal Solution Reached (Pulp)")
    for var in x.values():
        print(f"{var.name}: {var.value()}")
    print("Objective Value:", model.objective.value())


    # Solve with linprog (scipy) to compare
    result = linprog(
        c=objective_coeffs,
        A_ub=[[-coeff for coeff in row] if t == '>=' else row for row, t in zip(constraint_coeffs, constraint_types)],
        b_ub=[-b if t == '>=' else b for b, t in zip(b_values, constraint_types)],
        bounds=(0, None)  # Assuming non-negative variables
    )

    print("\nOptimal Solution Reached (linprog - scipy)")
    if result.success:
        print("Solution:", result.x)
        print("Objective Value:", result.fun)
    else:
        print("linprog Status:", result.message)



def two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values):
    """
    Performs the two-phase simplex method to solve a linear programming problem.

    Args:
        num_vars: Number of decision variables.
        num_constraints: Number of constraints.
        objective_coeffs: Coefficients of the objective function.
        constraint_coeffs: Coefficients of the constraints.
        constraint_types: Types of the constraints ('<=', '>=', or '=').
        b_values: Right-hand side values of the constraints.

    Returns:
        None. Prints the solution and the optimal objective value.
    """
    from pulp import LpMaximize, LpProblem, LpVariable, lpSum
    from scipy.optimize import linprog

    # Phase 1: Create the initial tableau and solve Phase 1
    tableau, tableau_metadata = create_tableau_two_phase_maximization(
        num_vars, num_constraints, constraint_coeffs, constraint_types, b_values
    )

    tableau_metadata["constraints"] = {
        "coeffs": constraint_coeffs,
        "types": constraint_types,
        "rhs": b_values
    }

    # Add tableau to tableau_metadata
    tableau_metadata["tableau"] = tableau

    basis = tableau_metadata["basis"]
    all_vars = tableau_metadata["all_vars"]
    coeffs = tableau_metadata["coeffs"]

    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    print("\nInitial Tableau (Phase 1):")
    print_tableau_maximization(tableau, all_vars, basis, coeffs, constraint_types, phase=1)

    # Phase 1 simplex iterations to remove artificial variables
    is_optimal_phase1 = False
    is_unbounded = False
    iteration_count = 0

    while not is_optimal_phase1 and not is_unbounded:
        entering_column = identify_entering_column_maximization(tableau)
        if entering_column is None:
            is_optimal_phase1 = True
            break





























        leaving_row = identify_leaving_row_maximization(tableau, entering_column)
        if leaving_row is None:
            is_unbounded = True
            break

        pivot_element = locate_pivot_element_maximization(tableau, entering_column, leaving_row)
        tableau = update_key_row_maximization(tableau, leaving_row, pivot_element)
        tableau = update_non_key_rows_maximization(tableau, entering_column, leaving_row)

        update_basis_with_values_maximization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

        print_tableau_maximization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=1)

        iteration_count += 1
        if iteration_count > 1000:
            print("Max iterations reached in Phase 1, stopping.")
            break

    # Check feasibility after Phase 1 iterations
    is_feasible, artificial_in_basis = check_phase_1_feasibility(tableau, tableau_metadata)

    if is_feasible:
        print("\nPhase 1 completed successfully, proceeding to Phase 2.")





        # ---  Recalculate rows after Phase 1 ---
        for i in range(num_constraints):
            pivot_element = tableau[i, basis[i]]
            if not np.isclose(pivot_element, 1):  # Check if the pivot element is not already 1
                tableau = update_key_row_maximization(tableau, i, pivot_element)
                tableau = update_non_key_rows_maximization(tableau, basis[i], i)

        # Transition to Phase 2
        tableau, tableau_metadata = transition_to_phase_2_maximization(tableau, objective_coeffs, tableau_metadata)

        # Update tableau_metadata["coeffs"] with the original objective coefficients
        tableau_metadata["coeffs"][:num_vars] = objective_coeffs  # Ensure coeffs is updated

        # Update the objective row for Phase 2
        update_objective_row_maximization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

        print("\nStarting Phase 2 with updated objective coefficients:")

        # Now print the tableau (coeffs should be correctly updated)
        print_tableau_maximization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)



        # Phase 2 simplex iterations
        is_optimal_phase2 = False
        iteration_count = 0
        while not is_optimal_phase2 and not is_unbounded:
            entering_column = identify_entering_column_maximization(tableau)
            if entering_column is None:
                is_optimal_phase2 = True
                break

            leaving_row = identify_leaving_row_maximization(tableau, entering_column)
            if leaving_row is None:
                is_unbounded = True
                break

            pivot_element = locate_pivot_element_maximization(tableau, entering_column, leaving_row)
            tableau = update_key_row_maximization(tableau, leaving_row, pivot_element)
            tableau = update_non_key_rows_maximization(tableau, entering_column, leaving_row)

            update_basis_with_values_maximization(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars, all_vars)

            # Ensure the objective row is updated after each pivot in Phase 2
            update_objective_row_maximization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

            print_tableau_maximization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)

            iteration_count += 1
            if iteration_count > 1000:
                print("Max iterations reached in Phase 2, stopping.")
                break

        # Extract and print the final solution after Phase 2
        if is_optimal_phase2:
            print("\nPhase 2 - Optimal Solution Reached")
            solution = extract_solution_maximization(tableau_metadata, 2)
            print(f"Optimal Objective Value: Z = {solution['objective_value']}")
            print("Solution:", solution['variable_values'])

            # Print the final tableau
            print("\nFinal Tableau (Phase 2):")
            print_tableau_maximization(tableau, tableau_metadata["all_vars"], tableau_metadata["basis"], tableau_metadata["coeffs"], constraint_types, phase=2)





            # --- Check for alternative optimal solutions ---

            alternative_solutions = []
            for j in range(num_vars):  # Check decision variables
                if j not in tableau_metadata["basis"] and abs(tableau[-1, j]) < 1e-10:  # Non-basic with near-zero reduced cost
                    print("Alternative optimal solutions exist!")
                    alternative_solutions.append(extract_solution_maximization(tableau_metadata, 2))  # Extract current solution

                    # Perform a pivot to find the alternative solution
                    leaving_row = identify_leaving_row_maximization(tableau, j)
                    if leaving_row is not None:
                        pivot_element = locate_pivot_element_maximization(tableau, j, leaving_row)
                        if pivot_element is not None:
                            tableau = update_key_row_maximization(tableau, leaving_row, pivot_element)
                            tableau = update_non_key_rows_maximization(tableau, j, leaving_row)
                            update_basis_with_values_maximization(tableau, tableau_metadata, j, leaving_row, artificial_vars, all_vars)
                            update_objective_row_maximization(tableau, objective_coeffs, tableau_metadata["basis"], artificial_vars, all_vars)

                            # Extract the alternative solution
                            alternative_solutions.append(extract_solution_maximization(tableau_metadata, 2))

            # Print alternative solutions (if found)
            if alternative_solutions:
                print("\nAlternative Optimal Solutions:")
                for sol in alternative_solutions:
                    print(sol)







    else:
        print("Phase 1 failed: Infeasible solution, artificial variables remain in the basis.")

    # Solve the maximization problem using PuLP for comparison
    model = LpProblem(name="Maximization_Problem", sense=LpMaximize)
    x = {i: LpVariable(name=f"x{i+1}", lowBound=0) for i in range(num_vars)}
    model += lpSum(objective_coeffs[i] * x[i] for i in range(num_vars))  # Maximization objective

    for i in range(num_constraints):
        if constraint_types[i] == '<=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) <= b_values[i]
        elif constraint_types[i] == '>=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) >= b_values[i]
        elif constraint_types[i] == '=':
            model += lpSum(constraint_coeffs[i][j] * x[j] for j in range(num_vars)) == b_values[i]

    # Solve the maximization problem using PuLP
    model.solve()

    print("\nOptimal Solution Reached (Pulp)")
    for var in x.values():
        print(f"{var.name}: {var.value()}")
    print("Objective Value:", model.objective.value())

    # Solve with linprog (scipy) to compare
    result = linprog(
        c=[-coeff for coeff in objective_coeffs],  # Negate the objective coefficients for maximization
        A_ub=[[-coeff for coeff in row] if t == '>=' else row for row, t in zip(constraint_coeffs, constraint_types)],
        b_ub=[-b if t == '>=' else b for b, t in zip(b_values, constraint_types)],
        bounds=(0, None)  # Assuming non-negative variables
    )

    # Convert the minimized objective back to maximization
    print("\nOptimal Solution Reached (linprog - scipy)")
    if result.success:
        print("Solution:", result.x)
        print("Objective Value:", -result.fun)  # Negate the minimized objective to get the maximized value
    else:
        print("linprog Status:", result.message)






def relax_constraints(constraint_coeffs, constraint_types, b_values, relaxation_factor=0.1):
    """
    Relaxes constraints.

    Args:
        constraint_coeffs: List of coefficients for each constraint.
        constraint_types: List of constraint types ('<=', '>=', '=').
        b_values: List of RHS values for each constraint.
        relaxation_factor: Factor by which to relax the constraints.

    Returns:
        relaxed_b_values: New list of RHS values after relaxation.
    """
    relaxed_b_values = b_values.copy()
    for i in range(len(b_values)):
        if constraint_types[i] == '<=':
            relaxed_b_values[i] += abs(relaxation_factor * b_values[i])  # Increase RHS for '<='
        elif constraint_types[i] == '>=':
            relaxed_b_values[i] -= abs(relaxation_factor * b_values[i])  # Decrease RHS for '>='
    return relaxed_b_values



def add_penalty_terms(tableau, tableau_metadata, penalty_parameters):
    """
    Adds penalty terms to the objective function.
    """
    num_original_vars = len(tableau_metadata['constraints']['coeffs'][0])  # Number of original decision variables
    basis = tableau_metadata['basis']
    constraint_coeffs = tableau_metadata['constraints']['coeffs']
    constraint_types = tableau_metadata['constraints']['types']

    # Create a new objective row with penalty terms
    new_objective_row = np.zeros(tableau.shape[1])

    for i in range(len(constraint_types)):
        penalty_param = penalty_parameters[i]
        if constraint_types[i] == '<=':
            # Add penalty to existing objective coefficients (only for original decision variables)
            new_objective_row[:num_original_vars] += penalty_param * np.array(constraint_coeffs[i])
        elif constraint_types[i] == '>=':
            new_objective_row[:num_original_vars] -= penalty_param * np.array(constraint_coeffs[i])

    # Add the original objective coefficients (only for original decision variables)
    new_objective_row[:num_original_vars] += np.array(tableau_metadata['coeffs'][:num_original_vars])

    # Calculate the new RHS for the objective row
    new_objective_row[-1] = -sum(new_objective_row[basis[i]] * tableau[i, -1] for i in range(len(basis)))

    # Update the objective row in the tableau
    tableau[-1, :] = new_objective_row

    # Update the objective coefficients in the metadata
    tableau_metadata['coeffs'] = new_objective_row[:num_original_vars].tolist()



def check_feasibility_after_iteration(tableau, tableau_metadata, num_vars, constraint_coeffs, constraint_types, b_values):
    """
    Checks whether the current solution is feasible after the first iteration by inspecting:
    1. If all Zj - Cj ≤ 0.
    2. If any constraints are violated.
    3. If any artificial variables remain in the basis with positive values.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: Metadata about the tableau (basis, all variables, etc.).
        num_vars: Number of decision variables.
        constraint_coeffs: List of coefficients for each constraint.
        constraint_types: List of the constraint types ('<=', '>=', '=').
        b_values: RHS values of the constraints.

    Returns:
        is_feasible: Boolean indicating whether the solution is feasible or not.
    """
    basis = tableau_metadata["basis"]
    all_vars = tableau_metadata["all_vars"]
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    # Check if all Zj - Cj ≤ 0
    zj_cj_row = tableau[-1, :num_vars]  # Only decision variables in Zj - Cj row
    if all(value <= 0 for value in zj_cj_row):
        print("\nSince all Zj - Cj ≤ 0:")

        # Extract the current solution values
        solution = extract_solution_minimization(tableau_metadata, phase=1)

        if solution is None or "variable_values" not in solution:
            print("Error extracting solution.")
            return False

        if solution['variable_values']:  # Ensure that we have valid variable values to display
            print("Hence, an optimal solution is arrived with values of variables as:")
            for var, value in solution['variable_values'].items():
                if var.startswith("x"):  # Only print decision variables
                    print(f"{var} = {value}")

            # Display the objective value (Min z = 0 for Phase 1, since we drive artificial vars out)
            print(f"\nMin z = {solution['objective_value']}")

        # Check for any violations of constraints
        violations = check_constraint_violations(
            solution=solution,
            constraint_coeffs=constraint_coeffs,
            constraint_types=constraint_types,
            b_values=b_values,
            debug=True
        )

        # If violations exist, print the infeasibility message
        if violations:
            print("\nBut this solution is not feasible (and also not optimal) because the solution violates the following constraints:")
            print_violation_report(violations, all_vars, constraint_coeffs)

        # Check if any artificial variable is still in the basis with a positive value
        for var_idx in artificial_vars:
            if var_idx in basis:
                row_idx = basis.index(var_idx)
                artificial_value = tableau[row_idx, -1]  # RHS value for artificial variable
                if artificial_value > 0:
                    print(f"\nArtificial variable {all_vars[var_idx]} appears in the basis with positive value {artificial_value}")
                    print("So Phase 2 is not possible.\n")
                    return False

        # If no violations and no artificial variables are left, the solution is feasible
        print("No constraint violations and no artificial variables remaining. The solution is feasible.")
        return True

    # If not all Zj - Cj are ≤ 0, the solution is not yet optimal
    print("\nZj - Cj values are not all ≤ 0, continue iterating...\n")
    return False


def check_feasibility_after_iteration_maximization(tableau, tableau_metadata, num_vars, constraint_coeffs, constraint_types, b_values):
    """
    Checks whether the current solution is feasible after the first iteration by inspecting:
    1. If all Zj - Cj ≥ 0 (for maximization).
    2. If any constraints are violated.
    3. If any artificial variables remain in the basis with positive values.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: Metadata about the tableau (basis, all variables, etc.).
        num_vars: Number of decision variables.
        constraint_coeffs: List of coefficients for each constraint.
        constraint_types: List of the constraint types ('<=', '>=', '=').
        b_values: RHS values of the constraints.

    Returns:
        is_feasible: Boolean indicating whether the solution is feasible or not.
    """
    basis = tableau_metadata["basis"]
    all_vars = tableau_metadata["all_vars"]
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    # Check if all Zj - Cj ≥ 0 (for maximization)
    zj_cj_row = tableau[-1, :num_vars]  # Only decision variables in Zj - Cj row
    if all(value >= 0 for value in zj_cj_row):
        print("\nSince all Zj - Cj ≥ 0:")

        # Extract the current solution values
        solution = extract_solution_minimization(tableau_metadata, phase=1)

        if solution is None or "variable_values" not in solution:
            print("Error extracting solution.")
            return False

        if solution['variable_values']:  # Ensure that we have valid variable values to display
            print("Hence, an optimal solution is arrived with values of variables as:")
            for var, value in solution['variable_values'].items():
                if var.startswith("x"):  # Only print decision variables
                    print(f"{var} = {value}")

            # Display the objective value (Max z for Phase 1)
            print(f"\nMax z = {solution['objective_value']}")

        # Check for any violations of constraints
        violations = check_constraint_violations(
            solution=solution,
            constraint_coeffs=constraint_coeffs,
            constraint_types=constraint_types,
            b_values=b_values,
            debug=True
        )

        # If violations exist, print the infeasibility message
        if violations:
            print("\nBut this solution is not feasible (and also not optimal) because the solution violates the following constraints:")
            print_violation_report(violations, all_vars, constraint_coeffs)

        # Check if any artificial variable is still in the basis with a positive value
        for var_idx in artificial_vars:
            if var_idx in basis:
                row_idx = basis.index(var_idx)
                artificial_value = tableau[row_idx, -1]  # RHS value for artificial variable
                if artificial_value > 0:
                    print(f"\nArtificial variable {all_vars[var_idx]} appears in the basis with positive value {artificial_value}")
                    print("So Phase 2 is not possible.\n")
                    return False

        # If no violations and no artificial variables are left, the solution is feasible
        print("No constraint violations and no artificial variables remaining. The solution is feasible.")
        return True

    # If not all Zj - Cj are ≥ 0, the solution is not yet optimal
    print("\nZj - Cj values are not all ≥ 0, continue iterating...\n")
    return False


def check_phase_1_feasibility(tableau, tableau_metadata):
    """
    Checks whether the solution after Phase 1 is feasible by ensuring that:
    1. No artificial variables remain in the basis with a positive value.

    Args:
        tableau: The current simplex tableau.
        tableau_metadata: Metadata containing information about the tableau.

    Returns:
        is_feasible: Boolean indicating if the solution is feasible.
        artificial_in_basis: Boolean indicating if any artificial variable remains in the basis.
    """
    basis = tableau_metadata["basis"]
    all_vars = tableau_metadata["all_vars"]
    artificial_vars = [i for i, var in enumerate(all_vars) if var.startswith('a')]

    is_feasible = True
    artificial_in_basis = False

    # Check for artificial variables in the basis
    for var_idx in artificial_vars:
        if var_idx in basis:
            row_idx = basis.index(var_idx)
            artificial_value = tableau[row_idx, -1]  # Check the RHS value of the artificial variable

            # If an artificial variable remains in the basis with a non-zero value, solution is infeasible
            if artificial_value > 0:
                print(f"Artificial variable {all_vars[var_idx]} is in the basis with value {artificial_value}.")
                artificial_in_basis = True
                is_feasible = False
            else:
                print(f"Artificial variable {all_vars[var_idx]} has left the basis or has zero value.")

    if not artificial_in_basis:
        print("No artificial variables remain in the basis with positive values. Phase 1 is feasible.")
    else:
        print("Phase 1 failed: Artificial variables remain in the basis with positive values.")

    return is_feasible, artificial_in_basis



def update_after_artificial_var_leaves_basis(tableau, tableau_metadata, entering_column, leaving_row, artificial_vars):
    """
    Updates the tableau when an artificial variable leaves the basis.
    Ensures the artificial variable's column and coefficient are zeroed out.
    """
    leaving_var_idx = tableau_metadata["basis"][leaving_row]

    # If the leaving variable is artificial, zero out its column
    if leaving_var_idx in artificial_vars:
        print(f"Artificial variable {leaving_var_idx} is leaving the basis. Zeroing out its column.")
        tableau[:, leaving_var_idx] = 0
        tableau_metadata["coeffs"][leaving_var_idx] = 0  # Set its coefficient to 0 in the objective row

    # Ensure that the artificial variable never re-enters the basis
    if entering_column in artificial_vars:
        tableau[:, entering_column] = 0  # Zero out the artificial variable's column
        tableau_metadata["coeffs"][entering_column] = 0  # Set its coefficient to 0 in the objective row


In [14]:
!pip install pulp

In [106]:
# Define the data
MAX_ITERATIONS = 1000
num_vars = 3
objective_coeffs = [5000, 4000, 6000]
num_constraints = 3
constraint_coeffs = [
    [3, 2, 1],  # Coefficients for constraint 1
    [1, 4, 3],  # Coefficients for constraint 2
    [1, 2, 2]   # Coefficients for constraint 3 (>= type)
]
constraint_types = ['<=', '<=', '>=']  # Types of constraints
b_values = [1200, 1500, 800]

# Call the two-phase simplex method
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤════════╤═════════╤══════╤══════╤══════╤════════════╤══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1     │ x2      │ x3   │ s1   │ s2   │ surplus3   │ a3   │ RHS   │
╞═══════════════════╪═════════╪════════╪═════════╪══════╪══════╪══════╪════════════╪══════╪═══════╡
│ BASIS             │ s1 = 0  │ s2 = 0 │ a3 = -1 │      │      │      │            │      │       │
├───────────────────┼─────────┼────────┼─────────┼──────┼──────┼──────┼────────────┼──────┼───────┤
│ Coeff             │ 0       │ 0      │ 0       │ 0    │ 0    │ 0    │ -1         │      │       │
├───────────────────┼─────────┼────────┼─────────┼──────┼──────┼──────┼────────────┼──────┼───────┤
│ <=                │ s1      │ 3      │ 2       │ 1    │ 1    │ 0    │ 0          │ 0    │ 1200  │
├───────────────────┼─────────┼────────┼─────────┼──────┼──────┼──────┼────────────┼──────┼───────┤
│ <=                │ s2      │ 1      │ 4   

In [107]:
# Define the data
MAX_ITERATIONS = 1000
num_vars = 10
objective_coeffs = [5, 3, 4, 6, 2, 7, 9, 4, 8, 10]
num_constraints = 12
constraint_coeffs = [
    [2, 3, 1, 5, 1, 4, 1, 1, 2, 1],
    [4, 1, 3, 1, 2, 1, 5, 1, 2, 3],
    [1, 1, 2, 3, 4, 1, 5, 3, 1, 1],
    [3, 2, 4, 1, 1, 3, 2, 4, 1, 2],
    [1, 2, 3, 4, 5, 1, 1, 1, 2, 3],
    [2, 3, 1, 1, 2, 5, 1, 4, 1, 1],
    [1, 4, 5, 2, 3, 6, 3, 1, 2, 1],
    [5, 1, 2, 1, 3, 4, 1, 1, 2, 5],
    [4, 2, 3, 1, 1, 2, 3, 4, 1, 1],
    [3, 1, 2, 5, 1, 4, 1, 1, 1, 2],
    [1, 1, 4, 3, 5, 1, 1, 1, 2, 3],
    [2, 3, 4, 1, 1, 2, 1, 5, 1, 2]
]
constraint_types = ['<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=']
b_values = [50, 40, 30, 60, 45, 50, 55, 35, 40, 70, 50, 65]

# Call the two-phase simplex method
# two_phase_simplex(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values, is_maximization=False)
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤═════════╤═════════╤════════╤═════════╤═════════╤════════╤═════════╤═════════╤═════════╤══════════╤══════════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤═══════╤═════════════╤═══════╤═══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1      │ x2      │ x3     │ x4      │ x5      │ x6     │ x7      │ x8      │ x9      │ x10      │ s1       │ surplus2   │ a2   │ a3   │ s4   │ surplus5   │ a5   │ a6   │ s7   │ surplus8   │ a8   │ a9   │ s10   │ surplus11   │ a11   │ a12   │ RHS   │
╞═══════════════════╪═════════╪═════════╪═════════╪════════╪═════════╪═════════╪════════╪═════════╪═════════╪═════════╪══════════╪══════════╪════════════╪══════╪══════╪══════╪════════════╪══════╪══════╪══════╪════════════╪══════╪══════╪═══════╪═════════════╪═══════╪═══════╪═══════╡
│ BASIS             │ s1 = 0  │ a2 = -1 │ a3 = -1 │ s4 = 0 │ a5 = -1 │ a6 = -1 │ s7 = 0 │ a8 = -

In [108]:
# Define the data
MAX_ITERATIONS = 1000
num_vars = 40
objective_coeffs = objective_coeffs = [5, 3, 4, 6, 2, 7, 9, 4, 8, 10, 12, 14, 15, 1, 7, 11, 5, 9, 13, 6,
                    10, 8, 5, 7, 2, 12, 13, 1, 9, 4, 3, 6, 11, 7, 15, 5, 4, 9, 8, 10]
num_constraints = 35
constraint_coeffs = constraint_coeffs = [
    [2, 3, 1, 5, 1, 4, 1, 1, 2, 1, 3, 2, 4, 1, 1, 5, 4, 3, 1, 2, 3, 2, 4, 1, 1, 3, 4, 2, 1, 3, 1, 2, 4, 3, 1, 4, 2, 1, 3, 5],
    [4, 1, 3, 1, 2, 1, 5, 1, 2, 3, 5, 2, 3, 1, 4, 3, 2, 1, 3, 2, 4, 3, 5, 1, 2, 3, 4, 5, 2, 3, 1, 2, 3, 1, 2, 4, 3, 2, 1, 4],
    [1, 1, 2, 3, 4, 1, 5, 3, 1, 1, 4, 3, 2, 4, 1, 1, 2, 4, 5, 3, 2, 4, 1, 1, 5, 2, 1, 3, 2, 4, 1, 5, 4, 2, 3, 1, 4, 5, 3, 1],
    [3, 4, 2, 1, 5, 3, 2, 4, 1, 5, 3, 1, 2, 4, 5, 3, 2, 4, 1, 5, 4, 3, 1, 2, 3, 5, 4, 1, 3, 2, 1, 5, 3, 4, 1, 2, 5, 3, 2, 4],
    [1, 5, 2, 4, 3, 2, 5, 1, 2, 4, 5, 3, 4, 1, 2, 5, 1, 3, 2, 5, 3, 1, 4, 2, 5, 1, 2, 3, 4, 1, 3, 5, 1, 2, 4, 3, 5, 2, 1, 4],
    [5, 3, 1, 4, 2, 3, 5, 2, 4, 5, 1, 2, 5, 3, 2, 4, 1, 5, 3, 4, 2, 5, 1, 2, 4, 3, 1, 5, 2, 1, 5, 3, 2, 4, 5, 1, 4, 3, 2, 5],
    [4, 2, 3, 5, 1, 4, 2, 5, 3, 2, 5, 1, 3, 4, 5, 2, 3, 5, 1, 2, 5, 4, 3, 1, 4, 5, 3, 1, 2, 4, 1, 5, 2, 3, 1, 4, 2, 5, 3, 4],
    [1, 4, 5, 2, 3, 1, 5, 3, 1, 5, 2, 3, 5, 1, 2, 4, 5, 1, 3, 4, 1, 2, 4, 5, 3, 1, 4, 2, 5, 1, 3, 2, 4, 1, 3, 5, 2, 5, 1, 3],
    [2, 3, 1, 5, 1, 3, 4, 1, 2, 5, 4, 3, 1, 5, 4, 2, 1, 3, 5, 1, 4, 2, 1, 5, 3, 4, 5, 2, 1, 3, 5, 2, 4, 1, 3, 5, 2, 1, 4, 3],
    [3, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 3, 2, 4, 1, 5, 2, 1, 4, 5, 3, 2, 1, 5, 4, 2, 1, 3, 5, 4, 2, 1, 5, 3, 1, 4, 2, 5, 3],
    [4, 3, 1, 2, 5, 4, 3, 1, 5, 2, 1, 3, 5, 2, 4, 1, 5, 3, 1, 2, 5, 4, 1, 5, 3, 2, 4, 1, 3, 5, 1, 4, 3, 2, 5, 4, 1, 3, 5, 2],
    [1, 4, 2, 3, 5, 1, 3, 4, 5, 2, 3, 1, 5, 2, 4, 5, 1, 3, 2, 5, 1, 4, 5, 2, 3, 1, 5, 4, 3, 2, 1, 5, 3, 4, 1, 5, 2, 4, 3, 5],
    [5, 1, 3, 2, 4, 5, 1, 4, 2, 5, 3, 1, 5, 4, 3, 1, 2, 5, 3, 1, 5, 2, 4, 1, 3, 5, 4, 1, 5, 3, 2, 1, 4, 5, 2, 1, 3, 5, 1, 4],
    [2, 5, 3, 4, 1, 5, 2, 3, 5, 1, 4, 2, 5, 1, 4, 3, 2, 5, 1, 5, 3, 2, 4, 1, 5, 2, 1, 5, 4, 3, 1, 5, 2, 1, 4, 5, 2, 1, 3, 5],
    [3, 1, 5, 2, 4, 3, 1, 5, 2, 4, 1, 3, 5, 2, 4, 1, 3, 2, 5, 1, 4, 3, 2, 5, 1, 3, 4, 2, 5, 1, 5, 4, 3, 1, 5, 2, 1, 5, 4, 3],
    [4, 5, 1, 2, 5, 4, 1, 3, 5, 2, 1, 5, 3, 2, 1, 4, 5, 1, 3, 4, 1, 5, 2, 3, 5, 1, 5, 4, 1, 3, 5, 2, 1, 4, 3, 5, 1, 5, 2, 4],
    [2, 1, 4, 5, 3, 2, 5, 1, 4, 5, 1, 3, 2, 5, 4, 1, 5, 1, 2, 5, 3, 1, 5, 2, 4, 1, 3, 5, 4, 1, 2, 3, 5, 1, 4, 3, 5, 2, 1, 5],
    [5, 3, 1, 2, 4, 5, 2, 1, 4, 5, 1, 5, 2, 3, 4, 1, 5, 1, 4, 3, 5, 2, 4, 1, 5, 3, 1, 5, 2, 4, 1, 5, 2, 1, 4, 3, 5, 4, 1, 2],
    [3, 4, 2, 5, 1, 3, 4, 1, 5, 2, 4, 1, 5, 3, 2, 1, 5, 3, 1, 4, 5, 2, 1, 5, 3, 4, 1, 2, 5, 3, 2, 4, 1, 5, 3, 1, 4, 5, 2, 3],
    [4, 3, 1, 5, 4, 2, 3, 5, 1, 2, 3, 4, 5, 2, 1, 3, 4, 1, 2, 5, 1, 5, 3, 1, 4, 5, 3, 2, 1, 5, 2, 1, 5, 4, 3, 5, 2, 4, 1, 3],
    [1, 5, 2, 4, 3, 2, 5, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 1, 4, 5, 3, 1, 5, 2, 4, 1, 3, 5, 1, 2, 5, 4, 1, 3, 5, 1, 4, 2, 5],
    [5, 4, 3, 1, 2, 5, 4, 2, 5, 1, 3, 2, 1, 5, 4, 3, 1, 5, 2, 4, 1, 5, 2, 3, 4, 1, 5, 3, 4, 1, 5, 2, 1, 4, 5, 2, 1, 3, 5, 1],
    [3, 5, 2, 1, 4, 3, 1, 5, 2, 4, 5, 3, 1, 5, 2, 4, 5, 1, 2, 5, 3, 4, 1, 5, 2, 4, 5, 3, 2, 1, 5, 4, 1, 3, 2, 5, 1, 3, 4, 5],
    [2, 4, 5, 1, 3, 5, 1, 4, 3, 5, 2, 1, 5, 4, 1, 3, 5, 2, 1, 5, 4, 3, 5, 1, 2, 4, 3, 5, 2, 1, 5, 4, 3, 1, 5, 2, 1, 5, 4, 3],
    [5, 2, 1, 5, 4, 3, 2, 1, 5, 4, 1, 5, 3, 4, 5, 2, 1, 5, 3, 1, 5, 4, 2, 1, 5, 3, 1, 5, 4, 3, 2, 5, 1, 4, 3, 1, 5, 2, 1, 4],
    [1, 3, 2, 5, 4, 1, 5, 2, 3, 5, 1, 4, 3, 2, 1, 5, 4, 1, 5, 3, 2, 1, 5, 4, 2, 1, 3, 5, 4, 1, 5, 2, 1, 4, 3, 5, 1, 5, 3, 2],
    [3, 1, 4, 5, 2, 3, 1, 5, 2, 4, 5, 3, 2, 5, 1, 4, 3, 2, 1, 5, 4, 5, 1, 2, 3, 4, 1, 5, 2, 3, 5, 4, 1, 5, 2, 1, 4, 3, 5, 1],
    [5, 4, 3, 1, 5, 2, 4, 3, 5, 1, 2, 3, 4, 1, 5, 2, 1, 5, 3, 2, 4, 5, 1, 2, 5, 4, 3, 1, 5, 2, 1, 3, 4, 5, 1, 5, 3, 2, 4, 1],
    [1, 5, 4, 2, 3, 5, 1, 3, 4, 5, 2, 1, 5, 3, 4, 1, 5, 2, 1, 4, 5, 2, 5, 1, 3, 4, 5, 2, 1, 3, 5, 4, 1, 5, 2, 1, 5, 4, 3, 2],
    [2, 1, 3, 4, 5, 2, 4, 5, 1, 3, 5, 1, 2, 5, 4, 3, 2, 1, 5, 4, 3, 2, 5, 1, 5, 3, 4, 2, 1, 5, 1, 4, 3, 2, 5, 1, 3, 4, 2, 1],
    [5, 2, 1, 5, 3, 4, 1, 5, 2, 1, 3, 4, 5, 2, 1, 5, 4, 1, 5, 2, 1, 4, 5, 1, 3, 5, 2, 4, 5, 1, 2, 5, 1, 4, 3, 5, 1, 2, 3, 4],
    [4, 3, 1, 2, 5, 1, 4, 5, 2, 3, 4, 5, 1, 3, 4, 2, 5, 1, 2, 4, 5, 3, 1, 5, 2, 3, 4, 1, 5, 2, 1, 5, 3, 1, 4, 5, 3, 2, 1, 4],
    [1, 5, 4, 2, 3, 5, 1, 4, 5, 2, 3, 1, 5, 4, 2, 1, 5, 1, 2, 4, 3, 1, 5, 2, 5, 1, 3, 4, 5, 2, 1, 5, 4, 1, 3, 5, 2, 5, 1, 4],
    [3, 4, 1, 2, 5, 3, 4, 5, 1, 2, 5, 3, 1, 4, 5, 3, 2, 4, 1, 5, 3, 1, 4, 2, 5, 3, 4, 1, 5, 3, 1, 4, 2, 1, 5, 3, 1, 4, 5, 2],
    [5, 2, 1, 5, 3, 2, 5, 1, 4, 5, 3, 1, 2, 5, 1, 4, 5, 3, 2, 5, 1, 3, 4, 1, 5, 2, 5, 1, 3, 4, 2, 5, 1, 5, 3, 1, 4, 2, 5, 1],
    [4, 1, 5, 3, 1, 4, 5, 2, 5, 1, 4, 3, 5, 1, 2, 5, 4, 1, 2, 5, 3, 1, 4, 5, 3, 1, 4, 2, 5, 3, 1, 4, 1, 5, 4, 3, 2, 5, 1, 2],
]

constraint_types = [
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=',  # First 10 constraint types
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=',  # Second set of 10 constraint types
    '<=', '>=', '=', '<=', '>=', '=', '<=', '>=', '=', '<=', '=', '<=', '>=', '<=', '<='   # Final 15 constraint types
]


b_values = [100, 200, 150, 120, 250, 180, 300, 130, 220, 170, 160, 140, 110, 210, 190,
            240, 260, 230, 270, 280, 290, 310, 320, 330, 340, 350, 360, 370, 380, 390,
            400, 410, 420, 430, 440]


# Call the two-phase simplex method
# two_phase_simplex(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values, is_maximization=False)
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤═════════╤═════════╤════════╤═════════╤═════════╤════════╤═════════╤═════════╤═════════╤═════════╤══════════╤══════════╤═════════╤══════════╤══════════╤═════════╤══════════╤══════════╤═════════╤═════════╤══════════╤══════════╤═════════╤══════════╤══════════╤═════════╤══════════╤══════════╤═════════╤══════════╤═════════╤══════════╤═════════╤═════════╤═══════╤═══════╤═══════╤═══════╤═══════╤═══════╤══════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1      │ x2      │ x3     │ x4      │ x5      │ x6     │ x7     

In [109]:
# Define the data
MAX_ITERATIONS = 1000
# Define the problem
num_vars = 15
objective_coeffs = [3, 5, 2, 7, 4, 6, 8, 3, 9, 1, 7, 5, 6, 4, 8]
num_constraints = 16
constraint_coeffs = [
    [1, 2, 3, 0, 0, 1, 2, 1, 3, 1, 0, 2, 4, 5, 1],  # Example constraint 1
    [0, 1, 1, 3, 2, 0, 1, 0, 1, 0, 3, 4, 2, 2, 3],  # Example constraint 2
    [2, 0, 3, 1, 1, 2, 0, 1, 0, 4, 1, 3, 2, 3, 1],  # Example constraint 3
    [1, 1, 0, 2, 1, 3, 2, 0, 5, 1, 2, 3, 0, 4, 2],  # Example constraint 4
    [0, 3, 1, 1, 2, 0, 1, 3, 2, 3, 1, 1, 3, 1, 2],  # Example constraint 5
    [2, 1, 0, 3, 1, 1, 2, 1, 4, 2, 3, 0, 1, 0, 3],  # Example constraint 6
    [3, 2, 1, 0, 3, 4, 1, 2, 1, 0, 5, 2, 1, 3, 1],  # Example constraint 7
    [0, 1, 3, 2, 0, 5, 1, 3, 4, 1, 2, 0, 3, 4, 5],  # Example constraint 8
    [4, 2, 0, 1, 3, 2, 5, 1, 0, 1, 3, 2, 1, 0, 2],  # Example constraint 9
    [1, 0, 2, 3, 1, 0, 4, 3, 1, 2, 3, 5, 4, 1, 2],  # Example constraint 10
    [3, 1, 1, 4, 0, 2, 1, 3, 2, 1, 4, 2, 3, 5, 1],  # Example constraint 11
    [2, 3, 0, 1, 2, 3, 4, 5, 1, 0, 2, 1, 0, 3, 2],  # Example constraint 12
    [1, 4, 3, 2, 0, 1, 5, 3, 0, 4, 1, 2, 5, 1, 3],  # Example constraint 13
    [3, 0, 2, 1, 3, 4, 2, 0, 5, 1, 3, 0, 2, 4, 1],  # Example constraint 14
    [2, 5, 1, 0, 4, 3, 1, 2, 3, 0, 4, 1, 3, 2, 5],  # Example constraint 15
    [0, 2, 4, 3, 1, 5, 3, 1, 0, 1, 2, 3, 4, 1, 2]   # Example constraint 16
]
constraint_types = ['<=', '<=', '>=', '=', '<=', '>=', '<=', '>=', '<=', '>=', '<=', '<=', '>=', '=', '<=', '>=']
b_values = [25, 30, 40, 15, 50, 10, 60, 45, 55, 35, 20, 25, 50, 15, 45, 30]

# Call the two-phase simplex method
# two_phase_simplex(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values, is_maximization=False)
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤════════╤═════════╤═════════╤════════╤═════════╤════════╤═════════╤════════╤══════════╤═════════╤═════════╤══════════╤══════════╤═════════╤══════════╤══════╤══════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤════════════╤══════╤══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╤═══════╤═════════════╤═══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1     │ x2      │ x3      │ x4     │ x5      │ x6     │ x7      │ x8     │ x9       │ x10     │ x11     │ x12      │ x13      │ x14     │ x15      │ s1   │ s2   │ surplus3   │ a3   │ a4   │ s5   │ surplus6   │ a6   │ s7   │ surplus8   │ a8   │ s9   │ surplus10   │ a10   │ s11   │ s12   │ surplus13   │ a13   │ a14   │ s15   │ surplus16   │ a16   │ RHS   │
╞═══════════════════╪═════════╪════════╪═════════╪═════════╪════════╪═════════╪════════╪═════════╪════════╪══════════╪═════════╪═════════╪══════════╪══════════╪═════

In [110]:
# Define the data
MAX_ITERATIONS = 1000
# Define the problem
num_vars = 10
objective_coeffs = [5, 4, 6, 3, 8, 2, 7, 9, 3, 5]
num_constraints = 8
constraint_coeffs = [
    [1, 0, 1, 0, 2, 1, 0, 0, 3, 2],  # Example constraint 1
    [2, 1, 0, 1, 3, 0, 1, 1, 0, 1],  # Example constraint 2
    [0, 1, 2, 0, 1, 3, 0, 2, 1, 1],  # Example constraint 3
    [1, 2, 3, 1, 0, 2, 1, 0, 2, 3],  # Example constraint 4
    [3, 1, 2, 3, 0, 1, 3, 1, 0, 1],  # Example constraint 5
    [0, 2, 1, 3, 1, 0, 2, 3, 1, 0],  # Example constraint 6
    [1, 1, 0, 2, 3, 2, 1, 0, 1, 2],  # Example constraint 7
    [2, 3, 1, 0, 1, 2, 0, 3, 1, 2],  # Example constraint 8
]
constraint_types = ['<=', '<=', '>=', '=', '<=', '>=', '<=', '>=']
b_values = [100, 200, 150, 80, 90, 120, 110, 140]  # Example RHS values

# Call the two-phase simplex method
# two_phase_simplex(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values,is_maximization=False)
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤════════╤═════════╤═════════╤════════╤═════════╤════════╤═════════╤══════╤══════╤═══════╤══════╤══════╤════════════╤══════╤══════╤══════╤════════════╤══════╤══════╤════════════╤══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1     │ x2      │ x3      │ x4     │ x5      │ x6     │ x7      │ x8   │ x9   │ x10   │ s1   │ s2   │ surplus3   │ a3   │ a4   │ s5   │ surplus6   │ a6   │ s7   │ surplus8   │ a8   │ RHS   │
╞═══════════════════╪═════════╪════════╪═════════╪═════════╪════════╪═════════╪════════╪═════════╪══════╪══════╪═══════╪══════╪══════╪════════════╪══════╪══════╪══════╪════════════╪══════╪══════╪════════════╪══════╪═══════╡
│ BASIS             │ s1 = 0  │ s2 = 0 │ a3 = -1 │ a4 = -1 │ s5 = 0 │ a6 = -1 │ s7 = 0 │ a8 = -1 │      │      │       │      │      │            │      │      │      │            │      │      │            │      │       │
├───────────────────┼─────────┼────────┼─────────

In [111]:
MAX_ITERATIONS = 1000
num_vars = 2
objective_coeffs = [6, 4]
num_constraints = 2
constraint_coeffs = [
    [1, 1],  # Example constraint 1
    [0, 1]   # Example constraint 2
]
constraint_types = ['<=', '>=']
b_values = [5, 8]  # RHS values


# Call the two-phase simplex method
# two_phase_simplex(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values, is_maximization=True)
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤═════════╤══════╤══════╤════════════╤══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1      │ x2   │ s1   │ surplus2   │ a2   │ RHS   │
╞═══════════════════╪═════════╪═════════╪══════╪══════╪════════════╪══════╪═══════╡
│ BASIS             │ s1 = 0  │ a2 = -1 │      │      │            │      │       │
├───────────────────┼─────────┼─────────┼──────┼──────┼────────────┼──────┼───────┤
│ Coeff             │ 0       │ 0       │ 0    │ 0    │ -1         │      │       │
├───────────────────┼─────────┼─────────┼──────┼──────┼────────────┼──────┼───────┤
│ <=                │ s1      │ 1       │ 1    │ 1    │ 0          │ 0    │ 5     │
├───────────────────┼─────────┼─────────┼──────┼──────┼────────────┼──────┼───────┤
│ >=                │ a2      │ 0       │ 1    │ 0    │ -1         │ 1    │ 8     │
├───────────────────┼─────────┼─────────┼──────┼──────┼────────────┼──────┼───────┤
│ Maximize          │

In [112]:
# Define the data
MAX_ITERATIONS = 1000
num_vars = 4
objective_coeffs = [4, 2, 3, 5]
num_constraints = 2
constraint_coeffs = [
    [2, 3, 4, 2],  # Coefficients for constraint 1
    [8, 1, 1, 5]  # Coefficients for constraint 2

]
constraint_types = ['=', '=']  # Types of constraints
b_values = [300, 300]

# Call the two-phase simplex method
two_phase_simplex_maximization(num_vars, num_constraints, objective_coeffs, constraint_coeffs, constraint_types, b_values)


Initial Tableau (Phase 1):

Simplex Tableau - Phase 1
╒═══════════════════╤═════════╤═════════╤══════╤══════╤══════╤══════╤══════╤═══════╕
│ Constraint Type   │ BASIS   │ x1      │ x2   │ x3   │ x4   │ a1   │ a2   │ RHS   │
╞═══════════════════╪═════════╪═════════╪══════╪══════╪══════╪══════╪══════╪═══════╡
│ BASIS             │ a1 = -1 │ a2 = -1 │      │      │      │      │      │       │
├───────────────────┼─────────┼─────────┼──────┼──────┼──────┼──────┼──────┼───────┤
│ Coeff             │ 0       │ 0       │ 0    │ 0    │ -1   │ -1   │      │       │
├───────────────────┼─────────┼─────────┼──────┼──────┼──────┼──────┼──────┼───────┤
│ =                 │ a1      │ 2       │ 3    │ 4    │ 2    │ 1    │ 0    │ 300   │
├───────────────────┼─────────┼─────────┼──────┼──────┼──────┼──────┼──────┼───────┤
│ =                 │ a2      │ 8       │ 1    │ 1    │ 5    │ 0    │ 1    │ 300   │
├───────────────────┼─────────┼─────────┼──────┼──────┼──────┼──────┼──────┼───────┤
│ Maximize